Dataset includes several time series representing different ATMs and their daily cash money demand at different locations.

In [1]:
# NOTE FIX THESE IMPORTS

from data_loader import convert_tsf_to_dataframe
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import statsmodels.api as sm
import math
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.nn.functional import linear, softmax
from torch.nn.modules.linear import NonDynamicallyQuantizableLinear
from torch import Tensor
from typing import Optional, Tuple, Union, Callable, Any, List
from torch.nn.init import xavier_uniform_, constant_, xavier_normal_
import copy
from torch.nn import Module, LayerNorm, ModuleList
from torch.nn.parameter import Parameter
import datetime
from torch.utils.data import Dataset, DataLoader
import sys

In [2]:
torch.set_printoptions(threshold=1000)

In [3]:
TSF_FILE = 'nn5_daily_dataset_with_missing_values.tsf'

In [4]:
data = convert_tsf_to_dataframe(TSF_FILE)

In [5]:
series_values = data[0]['series_value']

In [ ]:
data

In [ ]:
data[0]

In [ ]:
data[0]['series_value'][0]

In [ ]:
date_range_0 = pd.date_range(start='1996-03-18', periods=791, freq='D')

In [ ]:
date_range_0

In [ ]:
data_0 = pd.DataFrame({'series_value': data[0]['series_value'][0], 'date': date_range_0})
data_0 = data_0.set_index('date')

In [ ]:
data_0

In [ ]:
plt.plot(data_0['series_value'][:21])

In [ ]:
np.array(data_0['series_value'])

In [ ]:
# proportion of nulls and zeroes
total = 791 * 111
null_count = 0
zero_count = 0
for i in range(len(data[0]['series_value'])):
    series_values = np.array(pd.to_numeric(data[0]['series_value'][i], errors='coerce'))
    nulls_in_series = np.sum(np.isnan(series_values))
    null_count += nulls_in_series
    zeroes_in_series = len(series_values) - np.count_nonzero(series_values)
    zero_count += zeroes_in_series
(null_count + zero_count) / total
    

Questions and notes:

- Global methods seem better than traditional univariate methods for this dataset because we can leverage related but seperate datasets in a unified model. Traditional methods such as ARIMA do not have this capability and if we would need to fit a separate model for each dataset. (Look into this).  


- How to deal with missing values? I assume if we're using a deep learning method, we could simply treat the missing values as breakpoints for training samples. I.e. let's say you have \[$x_1$, $x_2$, $x_3$, $x_4$, $x_5$, $x_6$, $x_7$, $x_8$\] where this is a sequence in order of time and $x_5$ is missing. Then, assuming the model uses a lag of 2, we can treat {$X$: \[$x_1$, $x_2$\], $y$: $x_3$}, {$X$: \[$x_2$, $x_3$\], $y$: $x_4$} and {$X$: \[$x_6$, $x_7$\], $y$: $x_8$} as our training examples, treating $x_5$ as a breakpoint. Is there a better way? ANSWER: for now no need to interpolate missing data, let's just try training on what we have.


- How can we identify the types of seasonality in the data? Can we deal with multiple seasonality? Traditional seasonal decomposition methods (even those which deal with multiple seasonality i.e. MSTL) will probably not work too well due to the multiple series. How do we integrate seasonality into the model? One idea is to use sin/cos encodings depending on the seasonal position. I.e. for seasonality that occurs one day a week, use $a\sin (x\cdot \frac{\pi}{3.5})$ and the cos version, where $a$ is tuneable. But how many of these terms should we include? Seems like a relatively wieldy hyperparameter. Also, if we need to see how to modify the architecture to include these terms. Another idea is to include the previous season's data, i.e. alongside the $k$ lags from the past we use $x_{t - p}$ as input, where $p$ is the seasonal period. Note that we would also need some kind of positional encoding for this value. Perhaps try dealing with seasonality after an original attempt without it, though.


- TODO: I want to try applying a transformer model to this data, research and look into transformers. From there we can try different things. So first just try applying a vanilla transformer. 
    - BUT WAIT... is the transformer really the best choice here? The problem I see with the transformer is that it is more suited for sequence-to-sequence models. In other words, you get one complete sequence as input and have to output another related sequence. Perhaps there is some modification to this that allows for completion of one sequence but anyway, if I'm correct, the self-attention used in the transformer will not be applicable to numerical time series such as this one. When it comes to sequence-to-sequence models that the transformer is meant for, the words can influence each other, i.e. a word later in the sequence can provide semantic information about a word earlier in the sequence, and self-attention deals with that scenario, where the information flow is not necessarily left-to-right. But for a time series like this, the information flows unidirectionally, elements earlier in the sequence do not depend on elements later in the sequence. Using a self-attention encoding where all elements of the sequence attend on each other would lead to spurious modelling. Perhaps an RNN model would be more suited to this kind of time series data. I will look into deep learning models for time series and find something that makes sense. 



- Better way to decode? Right now training uses "teacher forcing", but inference does not, if a very wrong prediction is produced then it negatively affects the subsequent predictions that get decoded, and without a concept of sequence probability we can't use beam search. Perhaps predict everything at once, i.e. no autoregressive decoding (which is needed for NLP because you don't know when the sequence will end, but we know the desired forecast horizon for time series). New "decoder" takes timestep position, performs some positional embedding, computes attention on encoder output, depending on query generated from positional embedding, performs transformations on the values and outputs the desired number of forecasts, one for each positional embedding. Something to try. Note this could possibly also enable forecasting of variable length for a single trained model depending on how I implement the positional encodings. If I use a lookup table for the positional encodings this is impossible, but if I use matrix mulitplications with the raw timestep number it is possible.


- Seasonailty: first create a seasonal encoder. Essentially given a forecast horizon, i.e. 7, and a hyperparameter for window size, i.e. 5, we create a "seasonal context" of len (horizon + window_sz) - 1. In other words, we take all our desired dates to forecast, seasonally shifted, get those values, as well as the (window_sz - 1) / 2 values on each side. So we have our seasonal context, comprised of horizon_len windows of length window_sz. Example: if our context is \[1, 2, 3, 4, 5\] and our window_sz is 3 (meaning we want to forecast 3 into the future), we have 3 windows \[1, 2, 3\], \[2, 3, 4\], and \[3, 4, 5\]. One corresponding to each position we want to decode. The intuition is that we hope each window contains seasonal data relevant to each date we want to forecast. We encode this seasonal context with its own learned position embeddings and weights; encoder is our modified encoder with causal self attention. Once the self attention finishes, we get a matrix of size (context_len x d_season). Normally we would then use the decoder-encoder attention as in the normal transformer but the problem here is that if we want to use this with the modified decoder as above, we can't do this. The decoder inputs for the modified decoder are merely timestep encodings so I'm not sure if that will give enough information to attend to the seasonal context, but I should probably try it nonetheless. My idea is to first perform attention from the decoder timestep encodings to the encodings of the previous $k$ time series elements immediately preceding the dates we want to forecast. Then we attend from the output of this to the seasonal encodings, applying as mask (see notes) before the softmax so that each decoder position only attends to the corresponding window for each season. We perform this attention on each seasonal component at the same time by concatentating the keys along the position axis. From here we get the regular dimension of values which we transform to get all the decoder timesteps at once. 


- Think about feeature engineering


- How to deal with nulls in target? I.e. how do we remove these from loss? We might still have to discard data... Like if at timestep 3 in the decoder the ground truth isn't available, i.e. null, how can we compute the loss and keep it differentiable? 
    - I suppose we could impute the null value in the target to be the same as the previous value or something. Not ideal but will be differentiable at least
    - Pytorch has a reduce flag in loss which lets you do perform loss elementwise. Idea is that we remove the nulls after doing this, and average the rest. But is this differentiable? Well apparently it's somehow differentiable but some of the gradients become null
    
    
- Perhaps I should apply some sort of clustering method. It seems like each ATM is at a different location, so the location itself is a latent variable that is not explicitly included. Different locations and location types may look different. Clustering could deal with this, use a different model for each cluster. Hopefully these inherent location differences get picked up by the clustering method. Look into time series clustering. 


- Here's the plan: try a variety of different models, and forecast for 1-day, 2-days, ..., 7-days ahead

- Models to consider:
    - ARIMA (baseline)
    - LSTM
    - Transformer
    - Temporal fusion transformer


- Transformer ideas:
    - Deal with nulls by setting them to 0 and applying an (input) mask which we add before the softmax which makes the null components of the self-attention negative infinity, becoming 0 after the softmax, thus negating their attention weights and ensuring they do not factor in to the final result. Experimentally verified that this does not affect the backprop computation (null component has 0 gradient in query/key matrices). 
        - Note that we also have to mask out the row of the queries for the null value, only way I can think of to do this is to first let the softmax do its thing on the row of 0's, then remove the row (using the null timestep dim input), and add in a row of 0's at the deleted position. Wouldn't this break the differentiable graph though? Perhaps there's no need to do this after all. Let's verify. Yes, we don't need to do the initial removal from the softmax tensor, we can simply add a mask in the decoding component which masks out the encoding corresponding to null in its attention
    - Mask out future timesteps during encoding. I.e. make the encoder self attention autoregressive by applying an encoding mask. Deals with the issue mentioned above. So the encoding at position 2 can only be affected by positions 1 and 2, etc.
    

In [ ]:
# Trying vanilla transformer from pytorch with adaptations

In [6]:

def _in_projection_packed(
    q: Tensor,
    k: Tensor,
    v: Tensor,
    w: Tensor,
    b: Optional[Tensor] = None,
) -> List[Tensor]:
    r"""
    Performs the in-projection step of the attention operation, using packed weights.
    Output is a triple containing projection tensors for query, key and value.
    Args:
        q, k, v: query, key and value tensors to be projected. For self-attention,
            these are typically the same tensor; for encoder-decoder attention,
            k and v are typically the same tensor. (We take advantage of these
            identities for performance if they are present.) Regardless, q, k and v
            must share a common embedding dimension; otherwise their shapes may vary.
        w: projection weights for q, k and v, packed into a single tensor. Weights
            are packed along dimension 0, in q, k, v order.
        b: optional projection biases for q, k and v, packed into a single tensor
            in q, k, v order.
    Shape:
        Inputs:
        - q: :math:`(..., E)` where E is the embedding dimension
        - k: :math:`(..., E)` where E is the embedding dimension
        - v: :math:`(..., E)` where E is the embedding dimension
        - w: :math:`(E * 3, E)` where E is the embedding dimension
        - b: :math:`E * 3` where E is the embedding dimension
        Output:
        - in output list :math:`[q', k', v']`, each output tensor will have the
            same shape as the corresponding input tensor.
    """
    E = q.size(-1)
    if k is v:
        if q is k:
            # self-attention
            return linear(q, w, b).chunk(3, dim=-1)
        else:
            # encoder-decoder attention
            w_q, w_kv = w.split([E, E * 2])
            if b is None:
                b_q = b_kv = None
            else:
                b_q, b_kv = b.split([E, E * 2])
            return (linear(q, w_q, b_q),) + linear(k, w_kv, b_kv).chunk(2, dim=-1)
    else:
        w_q, w_k, w_v = w.chunk(3)
        if b is None:
            b_q = b_k = b_v = None
        else:
            b_q, b_k, b_v = b.chunk(3)
        return linear(q, w_q, b_q), linear(k, w_k, b_k), linear(v, w_v, b_v)

    
def _in_projection(
    q: Tensor,
    k: Tensor,
    v: Tensor,
    w_q: Tensor,
    w_k: Tensor,
    w_v: Tensor,
    b_q: Optional[Tensor] = None,
    b_k: Optional[Tensor] = None,
    b_v: Optional[Tensor] = None,
) -> Tuple[Tensor, Tensor, Tensor]:
    r"""
    Performs the in-projection step of the attention operation. This is simply
    a triple of linear projections, with shape constraints on the weights which
    ensure embedding dimension uniformity in the projected outputs.
    Output is a triple containing projection tensors for query, key and value.
    Args:
        q, k, v: query, key and value tensors to be projected.
        w_q, w_k, w_v: weights for q, k and v, respectively.
        b_q, b_k, b_v: optional biases for q, k and v, respectively.
    Shape:
        Inputs:
        - q: :math:`(Qdims..., Eq)` where Eq is the query embedding dimension and Qdims are any
            number of leading dimensions.
        - k: :math:`(Kdims..., Ek)` where Ek is the key embedding dimension and Kdims are any
            number of leading dimensions.
        - v: :math:`(Vdims..., Ev)` where Ev is the value embedding dimension and Vdims are any
            number of leading dimensions.
        - w_q: :math:`(Eq, Eq)`
        - w_k: :math:`(Eq, Ek)`
        - w_v: :math:`(Eq, Ev)`
        - b_q: :math:`(Eq)`
        - b_k: :math:`(Eq)`
        - b_v: :math:`(Eq)`
        Output: in output triple :math:`(q', k', v')`,
         - q': :math:`[Qdims..., Eq]`
         - k': :math:`[Kdims..., Eq]`
         - v': :math:`[Vdims..., Eq]`
    """
    Eq, Ek, Ev = q.size(-1), k.size(-1), v.size(-1)
    assert w_q.shape == (Eq, Eq), f"expecting query weights shape of {(Eq, Eq)}, but got {w_q.shape}"
    assert w_k.shape == (Eq, Ek), f"expecting key weights shape of {(Eq, Ek)}, but got {w_k.shape}"
    assert w_v.shape == (Eq, Ev), f"expecting value weights shape of {(Eq, Ev)}, but got {w_v.shape}"
    assert b_q is None or b_q.shape == (Eq,), f"expecting query bias shape of {(Eq,)}, but got {b_q.shape}"
    assert b_k is None or b_k.shape == (Eq,), f"expecting key bias shape of {(Eq,)}, but got {b_k.shape}"
    assert b_v is None or b_v.shape == (Eq,), f"expecting value bias shape of {(Eq,)}, but got {b_v.shape}"
    return linear(q, w_q, b_q), linear(k, w_k, b_k), linear(v, w_v, b_v)



def _scaled_dot_product_attention(
    q: Tensor,
    k: Tensor,
    v: Tensor,
    attn_mask: Optional[Tensor] = None,
    dropout_p: float = 0.0,
) -> Tuple[Tensor, Tensor]:
    r"""
    Computes scaled dot product attention on query, key and value tensors, using
    an optional attention mask if passed, and applying dropout if a probability
    greater than 0.0 is specified.
    Returns a tensor pair containing attended values and attention weights.
    Args:
        q, k, v: query, key and value tensors. See Shape section for shape details.
        attn_mask: optional tensor containing mask values to be added to calculated
            attention. May be 2D or 3D; see Shape section for details.
        dropout_p: dropout probability. If greater than 0.0, dropout is applied.
    Shape:
        - q: :math:`(B, Nt, E)` where B is batch size, Nt is the target sequence length,
            and E is embedding dimension.
        - key: :math:`(B, Ns, E)` where B is batch size, Ns is the source sequence length,
            and E is embedding dimension.
        - value: :math:`(B, Ns, E)` where B is batch size, Ns is the source sequence length,
            and E is embedding dimension.
        - attn_mask: either a 3D tensor of shape :math:`(B, Nt, Ns)` or a 2D tensor of
            shape :math:`(Nt, Ns)`.
        - Output: attention values have shape :math:`(B, Nt, E)`; attention weights
            have shape :math:`(B, Nt, Ns)`
    """
    B, Nt, E = q.shape
    q = q / math.sqrt(E)

    # (B, Nt, E) x (B, E, Ns) -> (B, Nt, Ns)
    if attn_mask is not None:
        attn = torch.baddbmm(attn_mask, q, k.transpose(-2, -1))
    else:
        attn = torch.bmm(q, k.transpose(-2, -1))
    
#     print('attn before soft')
#     print(attn)
    attn = softmax(attn, dim=-1)
#     print('attn after soft')
#     print(attn)

    if dropout_p > 0.0:
        attn = F.dropout(attn, p=dropout_p)
    # (B, Nt, Ns) x (B, Ns, E) -> (B, Nt, E)
    output = torch.bmm(attn, v)
#     print('attn output')
#     print(output)
    return output, attn



def multi_head_attention_forward(
    query: Tensor,
    key: Tensor,
    value: Tensor,
    embed_dim_to_check: int,
    num_heads: int,
    in_proj_weight: Optional[Tensor],
    in_proj_bias: Optional[Tensor],
    bias_k: Optional[Tensor],
    bias_v: Optional[Tensor],
    add_zero_attn: bool,
    dropout_p: float,
    out_proj_weight: Tensor,
    out_proj_bias: Optional[Tensor],
    training: bool = True,
    key_padding_mask: Optional[Tensor] = None,
    need_weights: bool = True,
    attn_mask: Optional[Tensor] = None,
    use_separate_proj_weight: bool = False,
    q_proj_weight: Optional[Tensor] = None,
    k_proj_weight: Optional[Tensor] = None,
    v_proj_weight: Optional[Tensor] = None,
    static_k: Optional[Tensor] = None,
    static_v: Optional[Tensor] = None,
    average_attn_weights: bool = True,
    is_batched: bool = True,
) -> Tuple[Tensor, Optional[Tensor]]:
    r"""
    Args:
        query, key, value: map a query and a set of key-value pairs to an output.
            See "Attention Is All You Need" for more details.
        embed_dim_to_check: total dimension of the model.
        num_heads: parallel attention heads.
        in_proj_weight, in_proj_bias: input projection weight and bias.
        bias_k, bias_v: bias of the key and value sequences to be added at dim=0.
        add_zero_attn: add a new batch of zeros to the key and
                       value sequences at dim=1.
        dropout_p: probability of an element to be zeroed.
        out_proj_weight, out_proj_bias: the output projection weight and bias.
        training: apply dropout if is ``True``.
        key_padding_mask: if provided, specified padding elements in the key will
            be ignored by the attention. This is an binary mask. When the value is True,
            the corresponding value on the attention layer will be filled with -inf.
        need_weights: output attn_output_weights.
        attn_mask: 2D or 3D mask that prevents attention to certain positions. A 2D mask will be broadcasted for all
            the batches while a 3D mask allows to specify a different mask for the entries of each batch.
        use_separate_proj_weight: the function accept the proj. weights for query, key,
            and value in different forms. If false, in_proj_weight will be used, which is
            a combination of q_proj_weight, k_proj_weight, v_proj_weight.
        q_proj_weight, k_proj_weight, v_proj_weight, in_proj_bias: input projection weight and bias.
        static_k, static_v: static key and value used for attention operators.
        average_attn_weights: If true, indicates that the returned ``attn_weights`` should be averaged across heads.
            Otherwise, ``attn_weights`` are provided separately per head. Note that this flag only has an effect
            when ``need_weights=True.``. Default: True
    Shape:
        Inputs:
        - query: :math:`(L, E)` or :math:`(L, N, E)` where L is the target sequence length, N is the batch size, E is
          the embedding dimension.
        - key: :math:`(S, E)` or :math:`(S, N, E)`, where S is the source sequence length, N is the batch size, E is
          the embedding dimension.
        - value: :math:`(S, E)` or :math:`(S, N, E)` where S is the source sequence length, N is the batch size, E is
          the embedding dimension.
        - key_padding_mask: :math:`(S)` or :math:`(N, S)` where N is the batch size, S is the source sequence length.
          If a ByteTensor is provided, the non-zero positions will be ignored while the zero positions
          will be unchanged. If a BoolTensor is provided, the positions with the
          value of ``True`` will be ignored while the position with the value of ``False`` will be unchanged.
        - attn_mask: 2D mask :math:`(L, S)` where L is the target sequence length, S is the source sequence length.
          3D mask :math:`(N*num_heads, L, S)` where N is the batch size, L is the target sequence length,
          S is the source sequence length. attn_mask ensures that position i is allowed to attend the unmasked
          positions. If a ByteTensor is provided, the non-zero positions are not allowed to attend
          while the zero positions will be unchanged. If a BoolTensor is provided, positions with ``True``
          are not allowed to attend while ``False`` values will be unchanged. If a FloatTensor
          is provided, it will be added to the attention weight.
        - static_k: :math:`(N*num_heads, S, E/num_heads)`, where S is the source sequence length,
          N is the batch size, E is the embedding dimension. E/num_heads is the head dimension.
        - static_v: :math:`(N*num_heads, S, E/num_heads)`, where S is the source sequence length,
          N is the batch size, E is the embedding dimension. E/num_heads is the head dimension.
        Outputs:
        - attn_output: :math:`(L, E)` or :math:`(L, N, E)` where L is the target sequence length, N is the batch size,
          E is the embedding dimension.
        - attn_output_weights: Only returned when ``need_weights=True``. If ``average_attn_weights=True``, returns
          attention weights averaged across heads of shape :math:`(L, S)` when input is unbatched or
          :math:`(N, L, S)`, where :math:`N` is the batch size, :math:`L` is the target sequence length, and
          :math:`S` is the source sequence length. If ``average_weights=False``, returns attention weights per
          head of shape :math:`(num_heads, L, S)` when input is unbatched or :math:`(N, num_heads, L, S)`.
    """
    
#     print('query')
#     print(query)
#     print('key')
#     print(key)
#     print('value')
#     print(value)
    
    
    # For unbatched input, we unsqueeze at the expected batch-dim to pretend that the input
    # is batched, run the computation and before returning squeeze the
    # batch dimension so that the output doesn't carry this temporary batch dimension.
    if not is_batched:
        # unsqueeze if the input is unbatched
        query = query.unsqueeze(1)
        key = key.unsqueeze(1)
        value = value.unsqueeze(1)
        if key_padding_mask is not None:
            key_padding_mask = key_padding_mask.unsqueeze(0)

    # set up shape vars
    tgt_len, bsz, embed_dim = query.shape
    src_len, _, _ = key.shape
    assert embed_dim == embed_dim_to_check, \
        f"was expecting embedding dimension of {embed_dim_to_check}, but got {embed_dim}"
    
    head_dim = embed_dim // num_heads
    assert head_dim * num_heads == embed_dim, f"embed_dim {embed_dim} not divisible by num_heads {num_heads}"
    if use_separate_proj_weight:
        # allow MHA to have different embedding dimensions when separate projection weights are used
        assert key.shape[:2] == value.shape[:2], \
            f"key's sequence and batch dims {key.shape[:2]} do not match value's {value.shape[:2]}"
    else:
        assert key.shape == value.shape, f"key shape {key.shape} does not match value shape {value.shape}"

    #
    # compute in-projection
    #
 
    if not use_separate_proj_weight:
        assert in_proj_weight is not None, "use_separate_proj_weight is False but in_proj_weight is None"
        q, k, v = _in_projection_packed(query, key, value, in_proj_weight, in_proj_bias)
    else:
        assert q_proj_weight is not None, "use_separate_proj_weight is True but q_proj_weight is None"
        assert k_proj_weight is not None, "use_separate_proj_weight is True but k_proj_weight is None"
        assert v_proj_weight is not None, "use_separate_proj_weight is True but v_proj_weight is None"
        if in_proj_bias is None:
            b_q = b_k = b_v = None
        else:
            b_q, b_k, b_v = in_proj_bias.chunk(3)
        q, k, v = _in_projection(query, key, value, q_proj_weight, k_proj_weight, v_proj_weight, b_q, b_k, b_v)

#     print('query_emb')
#     print(q)
#     print('key_emb')
#     print(k)
#     print('value_emb')
#     print(v)
    # prep attention mask
    if attn_mask is not None:
        if attn_mask.dtype == torch.uint8:
            warnings.warn("Byte tensor for attn_mask in nn.MultiheadAttention is deprecated. Use bool tensor instead.")
            attn_mask = attn_mask.to(torch.bool)
        else:
            assert attn_mask.is_floating_point() or attn_mask.dtype == torch.bool, \
                f"Only float, byte, and bool types are supported for attn_mask, not {attn_mask.dtype}"
        # ensure attn_mask's dim is 3
        if attn_mask.dim() == 2:
            correct_2d_size = (tgt_len, src_len)
            if attn_mask.shape != correct_2d_size:
                raise RuntimeError(f"The shape of the 2D attn_mask is {attn_mask.shape}, but should be {correct_2d_size}.")
            attn_mask = attn_mask.unsqueeze(0)
        elif attn_mask.dim() == 3:
            correct_3d_size = (bsz * num_heads, tgt_len, src_len)
            if attn_mask.shape != correct_3d_size:
                raise RuntimeError(f"The shape of the 3D attn_mask is {attn_mask.shape}, but should be {correct_3d_size}.")
        else:
            raise RuntimeError(f"attn_mask's dimension {attn_mask.dim()} is not supported")

    # prep key padding mask
    if key_padding_mask is not None and key_padding_mask.dtype == torch.uint8:
        warnings.warn("Byte tensor for key_padding_mask in nn.MultiheadAttention is deprecated. Use bool tensor instead.")
        key_padding_mask = key_padding_mask.to(torch.bool)

    # add bias along batch dimension (currently second)
    if bias_k is not None and bias_v is not None:
        assert static_k is None, "bias cannot be added to static key."
        assert static_v is None, "bias cannot be added to static value."
        k = torch.cat([k, bias_k.repeat(1, bsz, 1)])
        v = torch.cat([v, bias_v.repeat(1, bsz, 1)])
        if attn_mask is not None:
            attn_mask = pad(attn_mask, (0, 1))
        if key_padding_mask is not None:
            key_padding_mask = pad(key_padding_mask, (0, 1))
    else:
        assert bias_k is None
        assert bias_v is None

    #
    # reshape q, k, v for multihead attention and make em batch first
    #
    q = q.contiguous().view(tgt_len, bsz * num_heads, head_dim).transpose(0, 1)  
    if static_k is None:
        k = k.contiguous().view(k.shape[0], bsz * num_heads, head_dim).transpose(0, 1)
    else:
        # TODO finish disentangling control flow so we don't do in-projections when statics are passed
        assert static_k.size(0) == bsz * num_heads, \
            f"expecting static_k.size(0) of {bsz * num_heads}, but got {static_k.size(0)}"
        assert static_k.size(2) == head_dim, \
            f"expecting static_k.size(2) of {head_dim}, but got {static_k.size(2)}"
        k = static_k
    if static_v is None:
        v = v.contiguous().view(v.shape[0], bsz * num_heads, head_dim).transpose(0, 1)
    else:
        # TODO finish disentangling control flow so we don't do in-projections when statics are passed
        assert static_v.size(0) == bsz * num_heads, \
            f"expecting static_v.size(0) of {bsz * num_heads}, but got {static_v.size(0)}"
        assert static_v.size(2) == head_dim, \
            f"expecting static_v.size(2) of {head_dim}, but got {static_v.size(2)}"
        v = static_v

    # update source sequence length after adjustments
    src_len = k.size(1)

    # merge key padding and attention masks
    if key_padding_mask is not None:
        assert key_padding_mask.shape == (bsz, src_len), \
            f"expecting key_padding_mask shape of {(bsz, src_len)}, but got {key_padding_mask.shape}"
        key_padding_mask = key_padding_mask.view(bsz, 1, 1, src_len).   \
            expand(-1, num_heads, -1, -1).reshape(bsz * num_heads, 1, src_len)
        if attn_mask is None:
            attn_mask = key_padding_mask
        elif attn_mask.dtype == torch.bool:
            attn_mask = attn_mask.logical_or(key_padding_mask)
        else:
            attn_mask = attn_mask.masked_fill(key_padding_mask, float("-inf"))

    # convert mask to float
    if attn_mask is not None and attn_mask.dtype == torch.bool:
        new_attn_mask = torch.zeros_like(attn_mask, dtype=q.dtype)
        new_attn_mask.masked_fill_(attn_mask, float("-inf"))
        attn_mask = new_attn_mask

    # adjust dropout probability
    if not training:
        dropout_p = 0.0

    #
    # (deep breath) calculate attention and out projection
    #
    attn_output, attn_output_weights = _scaled_dot_product_attention(q, k, v, attn_mask, dropout_p)
    attn_output = attn_output.transpose(0, 1).contiguous().view(tgt_len * bsz, embed_dim)
    attn_output = F.linear(attn_output, out_proj_weight, out_proj_bias)
    attn_output = attn_output.view(tgt_len, bsz, attn_output.size(1))

    if need_weights:
        # optionally average attention weights over heads
        attn_output_weights = attn_output_weights.view(bsz, num_heads, tgt_len, src_len)
        if average_attn_weights:
            attn_output_weights = attn_output_weights.sum(dim=1) / num_heads

        if not is_batched:
            # squeeze the output if input was unbatched
            attn_output = attn_output.squeeze(1)
            attn_output_weights = attn_output_weights.squeeze(0)
        return attn_output, attn_output_weights
    else:
        if not is_batched:
            # squeeze the output if input was unbatched
            attn_output = attn_output.squeeze(1)
        return attn_output, None

In [7]:
class MultiheadAttention(nn.Module):
    r"""Allows the model to jointly attend to information
    from different representation subspaces as described in the paper:
    `Attention Is All You Need <https://arxiv.org/abs/1706.03762>`_.

    Multi-Head Attention is defined as:

    .. math::
        \text{MultiHead}(Q, K, V) = \text{Concat}(head_1,\dots,head_h)W^O

    where :math:`head_i = \text{Attention}(QW_i^Q, KW_i^K, VW_i^V)`.

    Args:
        embed_dim: Total dimension of the model.
        num_heads: Number of parallel attention heads. Note that ``embed_dim`` will be split
            across ``num_heads`` (i.e. each head will have dimension ``embed_dim // num_heads``).
        dropout: Dropout probability on ``attn_output_weights``. Default: ``0.0`` (no dropout).
        bias: If specified, adds bias to input / output projection layers. Default: ``True``.
        add_bias_kv: If specified, adds bias to the key and value sequences at dim=0. Default: ``False``.
        add_zero_attn: If specified, adds a new batch of zeros to the key and value sequences at dim=1.
            Default: ``False``.
        kdim: Total number of features for keys. Default: ``None`` (uses ``kdim=embed_dim``).
        vdim: Total number of features for values. Default: ``None`` (uses ``vdim=embed_dim``).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).

    Examples::

        >>> multihead_attn = nn.MultiheadAttention(embed_dim, num_heads)
        >>> attn_output, attn_output_weights = multihead_attn(query, key, value)
    """

    def __init__(self, embed_dim, num_heads, dropout=0., bias=True, add_bias_kv=False, add_zero_attn=False,
                 kdim=None, vdim=None, batch_first=False, device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(MultiheadAttention, self).__init__()
        self.embed_dim = embed_dim
        self.kdim = kdim if kdim is not None else embed_dim
        self.vdim = vdim if vdim is not None else embed_dim
        self._qkv_same_embed_dim = self.kdim == embed_dim and self.vdim == embed_dim

        self.num_heads = num_heads
        self.dropout = dropout
        self.batch_first = batch_first
        self.head_dim = embed_dim // num_heads
        assert self.head_dim * num_heads == self.embed_dim, "embed_dim must be divisible by num_heads"

        if self._qkv_same_embed_dim is False:
            self.q_proj_weight = Parameter(torch.empty((embed_dim, embed_dim), **factory_kwargs))
            self.k_proj_weight = Parameter(torch.empty((embed_dim, self.kdim), **factory_kwargs))
            self.v_proj_weight = Parameter(torch.empty((embed_dim, self.vdim), **factory_kwargs))
            self.register_parameter('in_proj_weight', None)
        else:
            self.in_proj_weight = Parameter(torch.empty((3 * embed_dim, embed_dim), **factory_kwargs))
            self.register_parameter('q_proj_weight', None)
            self.register_parameter('k_proj_weight', None)
            self.register_parameter('v_proj_weight', None)

        if bias:
            self.in_proj_bias = Parameter(torch.empty(3 * embed_dim, **factory_kwargs))
        else:
            self.register_parameter('in_proj_bias', None)
        self.out_proj = NonDynamicallyQuantizableLinear(embed_dim, embed_dim, bias=bias, **factory_kwargs)

        if add_bias_kv:
            self.bias_k = Parameter(torch.empty((1, 1, embed_dim), **factory_kwargs))
            self.bias_v = Parameter(torch.empty((1, 1, embed_dim), **factory_kwargs))
        else:
            self.bias_k = self.bias_v = None

        self.add_zero_attn = add_zero_attn

        self._reset_parameters()

    def _reset_parameters(self):
        if self._qkv_same_embed_dim:
            xavier_uniform_(self.in_proj_weight)
        else:
            xavier_uniform_(self.q_proj_weight)
            xavier_uniform_(self.k_proj_weight)
            xavier_uniform_(self.v_proj_weight)

        if self.in_proj_bias is not None:
            constant_(self.in_proj_bias, 0.)
            constant_(self.out_proj.bias, 0.)
        if self.bias_k is not None:
            xavier_normal_(self.bias_k)
        if self.bias_v is not None:
            xavier_normal_(self.bias_v)

    def __setstate__(self, state):
        # Support loading old MultiheadAttention checkpoints generated by v1.1.0
        if '_qkv_same_embed_dim' not in state:
            state['_qkv_same_embed_dim'] = True

        super(MultiheadAttention, self).__setstate__(state)

    def forward(self, query: Tensor, key: Tensor, value: Tensor, key_padding_mask: Optional[Tensor] = None,
                need_weights: bool = True, attn_mask: Optional[Tensor] = None,
                average_attn_weights: bool = True) -> Tuple[Tensor, Optional[Tensor]]:
        r"""
    Args:
        query: Query embeddings of shape :math:`(L, E_q)` for unbatched input, :math:`(L, N, E_q)` when ``batch_first=False``
            or :math:`(N, L, E_q)` when ``batch_first=True``, where :math:`L` is the target sequence length,
            :math:`N` is the batch size, and :math:`E_q` is the query embedding dimension ``embed_dim``.
            Queries are compared against key-value pairs to produce the output.
            See "Attention Is All You Need" for more details.
        key: Key embeddings of shape :math:`(S, E_k)` for unbatched input, :math:`(S, N, E_k)` when ``batch_first=False``
            or :math:`(N, S, E_k)` when ``batch_first=True``, where :math:`S` is the source sequence length,
            :math:`N` is the batch size, and :math:`E_k` is the key embedding dimension ``kdim``.
            See "Attention Is All You Need" for more details.
        value: Value embeddings of shape :math:`(S, E_v)` for unbatched input, :math:`(S, N, E_v)` when
            ``batch_first=False`` or :math:`(N, S, E_v)` when ``batch_first=True``, where :math:`S` is the source
            sequence length, :math:`N` is the batch size, and :math:`E_v` is the value embedding dimension ``vdim``.
            See "Attention Is All You Need" for more details.
        key_padding_mask: If specified, a mask of shape :math:`(N, S)` indicating which elements within ``key``
            to ignore for the purpose of attention (i.e. treat as "padding"). For unbatched `query`, shape should be :math:`(S)`.
            Binary and byte masks are supported.
            For a binary mask, a ``True`` value indicates that the corresponding ``key`` value will be ignored for
            the purpose of attention. For a byte mask, a non-zero value indicates that the corresponding ``key``
            value will be ignored.
        need_weights: If specified, returns ``attn_output_weights`` in addition to ``attn_outputs``.
            Default: ``True``.
        attn_mask: If specified, a 2D or 3D mask preventing attention to certain positions. Must be of shape
            :math:`(L, S)` or :math:`(N\cdot\text{num\_heads}, L, S)`, where :math:`N` is the batch size,
            :math:`L` is the target sequence length, and :math:`S` is the source sequence length. A 2D mask will be
            broadcasted across the batch while a 3D mask allows for a different mask for each entry in the batch.
            Binary, byte, and float masks are supported. For a binary mask, a ``True`` value indicates that the
            corresponding position is not allowed to attend. For a byte mask, a non-zero value indicates that the
            corresponding position is not allowed to attend. For a float mask, the mask values will be added to
            the attention weight.
        average_attn_weights: If true, indicates that the returned ``attn_weights`` should be averaged across
            heads. Otherwise, ``attn_weights`` are provided separately per head. Note that this flag only has an
            effect when ``need_weights=True.``. Default: True (i.e. average weights across heads)

    Outputs:
        - **attn_output** - Attention outputs of shape :math:`(L, E)` when input is unbatched,
          :math:`(L, N, E)` when ``batch_first=False`` or :math:`(N, L, E)` when ``batch_first=True``,
          where :math:`L` is the target sequence length, :math:`N` is the batch size, and :math:`E` is the
          embedding dimension ``embed_dim``.
        - **attn_output_weights** - Only returned when ``need_weights=True``. If ``average_attn_weights=True``,
          returns attention weights averaged across heads of shape :math:`(L, S)` when input is unbatched or
          :math:`(N, L, S)`, where :math:`N` is the batch size, :math:`L` is the target sequence length, and
          :math:`S` is the source sequence length. If ``average_weights=False``, returns attention weights per
          head of shape :math:`(num_heads, L, S)` when input is unbatched or :math:`(N, num_heads, L, S)`.

        .. note::
            `batch_first` argument is ignored for unbatched inputs.
        """
        
        is_batched = query.dim() == 3
        if self.batch_first and is_batched:
            query, key, value = [x.transpose(1, 0) for x in (query, key, value)]

        if not self._qkv_same_embed_dim:
            attn_output, attn_output_weights = multi_head_attention_forward(
                query, key, value, self.embed_dim, self.num_heads,
                self.in_proj_weight, self.in_proj_bias,
                self.bias_k, self.bias_v, self.add_zero_attn,
                self.dropout, self.out_proj.weight, self.out_proj.bias,
                training=self.training,
                key_padding_mask=key_padding_mask, need_weights=need_weights,
                attn_mask=attn_mask, use_separate_proj_weight=True,
                q_proj_weight=self.q_proj_weight, k_proj_weight=self.k_proj_weight,
                v_proj_weight=self.v_proj_weight, average_attn_weights=average_attn_weights)
        else:
            attn_output, attn_output_weights = multi_head_attention_forward(
                query, key, value, self.embed_dim, self.num_heads,
                self.in_proj_weight, self.in_proj_bias,
                self.bias_k, self.bias_v, self.add_zero_attn,
                self.dropout, self.out_proj.weight, self.out_proj.bias,
                training=self.training,
                key_padding_mask=key_padding_mask, need_weights=need_weights,
                attn_mask=attn_mask, average_attn_weights=average_attn_weights)
        if self.batch_first and is_batched:
            return attn_output.transpose(1, 0), attn_output_weights
        else:
            return attn_output, attn_output_weights
        


In [8]:
def _get_clones(module, N):
    return ModuleList([copy.deepcopy(module) for i in range(N)])



class TransformerModel(Module):
    r"""A transformer model. User is able to modify the attributes as needed. The architecture
    is based on the paper "Attention Is All You Need". Ashish Vaswani, Noam Shazeer,
    Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N Gomez, Lukasz Kaiser, and
    Illia Polosukhin. 2017. Attention is all you need. In Advances in Neural Information
    Processing Systems, pages 6000-6010.
    Args:
        d_model: the number of expected features in the encoder/decoder inputs (default=512).
        nhead: the number of heads in the multiheadattention models (default=8).
        num_encoder_layers: the number of sub-encoder-layers in the encoder (default=6).
        num_decoder_layers: the number of sub-decoder-layers in the decoder (default=6).
        dim_feedforward: the dimension of the feedforward network model (default=2048).
        dropout: the dropout value (default=0.1).
        activation: the activation function of encoder/decoder intermediate layer, can be a string
            ("relu" or "gelu") or a unary callable. Default: relu
        custom_encoder: custom encoder (default=None).
        custom_decoder: custom decoder (default=None).
        layer_norm_eps: the eps value in layer normalization components (default=1e-5).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).
        norm_first: if ``True``, encoder and decoder layers will perform LayerNorms before
            other attention and feedforward operations, otherwise after. Default: ``False`` (after).
    Examples::
        >>> transformer_model = nn.Transformer(nhead=16, num_encoder_layers=12)
        >>> src = torch.rand((10, 32, 512))
        >>> tgt = torch.rand((20, 32, 512))
        >>> out = transformer_model(src, tgt)
    Note: A full example to apply nn.Transformer module for the word language model is available in
    https://github.com/pytorch/examples/tree/master/word_language_model
    """

    def __init__(self, d_model: int = 512, nhead: int = 8, num_encoder_layers: int = 6,
                 num_decoder_layers: int = 6, dim_feedforward: int = 2048, dropout: float = 0.1,
                 activation: Union[str, Callable[[Tensor], Tensor]] = F.relu,
                 custom_encoder: Optional[Any] = None, custom_decoder: Optional[Any] = None,
                 layer_norm_eps: float = 1e-5, batch_first: bool = False, norm_first: bool = False,
                 use_norm=True,
                 device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(TransformerModel, self).__init__()

        if custom_encoder is not None:
            self.encoder = custom_encoder
        else:
            encoder_layer = TransformerEncoderLayer(d_model, nhead, dim_feedforward, dropout,
                                                    activation, layer_norm_eps, batch_first, norm_first, 
                                                    use_norm,
                                                    **factory_kwargs)
            encoder_norm = None
            if use_norm:
                encoder_norm = LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
            self.encoder = TransformerEncoder(encoder_layer, num_encoder_layers, encoder_norm)

        if custom_decoder is not None:
            self.decoder = custom_decoder
        else:
            decoder_layer = TransformerDecoderLayer(d_model, nhead, dim_feedforward, dropout,
                                                    activation, layer_norm_eps, batch_first, norm_first,
                                                    use_norm,
                                                    **factory_kwargs)
            decoder_norm = None
            if use_norm:
                decoder_norm = LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
            self.decoder = TransformerDecoder(decoder_layer, num_decoder_layers, decoder_norm)

        self._reset_parameters()

        self.d_model = d_model
        self.nhead = nhead

        self.batch_first = batch_first

    def forward(self, src: Tensor, tgt: Tensor, src_mask: Optional[Tensor] = None, tgt_mask: Optional[Tensor] = None,
                memory_mask: Optional[Tensor] = None, src_key_padding_mask: Optional[Tensor] = None,
                tgt_key_padding_mask: Optional[Tensor] = None, memory_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Take in and process masked source/target sequences.
        Args:
            src: the sequence to the encoder (required).
            tgt: the sequence to the decoder (required).
            src_mask: the additive mask for the src sequence (optional).
            tgt_mask: the additive mask for the tgt sequence (optional).
            memory_mask: the additive mask for the encoder output (optional).
            src_key_padding_mask: the ByteTensor mask for src keys per batch (optional).
            tgt_key_padding_mask: the ByteTensor mask for tgt keys per batch (optional).
            memory_key_padding_mask: the ByteTensor mask for memory keys per batch (optional).
        Shape:
            - src: :math:`(S, E)` for unbatched input, :math:`(S, N, E)` if `batch_first=False` or
              `(N, S, E)` if `batch_first=True`.
            - tgt: :math:`(T, E)` for unbatched input, :math:`(T, N, E)` if `batch_first=False` or
              `(N, T, E)` if `batch_first=True`.
            - src_mask: :math:`(S, S)` or :math:`(N\cdot\text{num\_heads}, S, S)`.
            - tgt_mask: :math:`(T, T)` or :math:`(N\cdot\text{num\_heads}, T, T)`.
            - memory_mask: :math:`(T, S)`.
            - src_key_padding_mask: :math:`(S)` for unbatched input otherwise :math:`(N, S)`.
            - tgt_key_padding_mask: :math:`(T)` for unbatched input otherwise :math:`(N, T)`.
            - memory_key_padding_mask: :math:`(S)` for unbatched input otherwise :math:`(N, S)`.
            Note: [src/tgt/memory]_mask ensures that position i is allowed to attend the unmasked
            positions. If a ByteTensor is provided, the non-zero positions are not allowed to attend
            while the zero positions will be unchanged. If a BoolTensor is provided, positions with ``True``
            are not allowed to attend while ``False`` values will be unchanged. If a FloatTensor
            is provided, it will be added to the attention weight.
            [src/tgt/memory]_key_padding_mask provides specified elements in the key to be ignored by
            the attention. If a ByteTensor is provided, the non-zero positions will be ignored while the zero
            positions will be unchanged. If a BoolTensor is provided, the positions with the
            value of ``True`` will be ignored while the position with the value of ``False`` will be unchanged.
            - output: :math:`(T, E)` for unbatched input, :math:`(T, N, E)` if `batch_first=False` or
              `(N, T, E)` if `batch_first=True`.
            Note: Due to the multi-head attention architecture in the transformer model,
            the output sequence length of a transformer is same as the input sequence
            (i.e. target) length of the decoder.
            where S is the source sequence length, T is the target sequence length, N is the
            batch size, E is the feature number
        Examples:
            >>> output = transformer_model(src, tgt, src_mask=src_mask, tgt_mask=tgt_mask)
        """

        is_batched = src.dim() == 3
        if not self.batch_first and src.size(1) != tgt.size(1) and is_batched:
            raise RuntimeError("the batch number of src and tgt must be equal")
        elif self.batch_first and src.size(0) != tgt.size(0) and is_batched:
            raise RuntimeError("the batch number of src and tgt must be equal")

        if src.size(-1) != self.d_model or tgt.size(-1) != self.d_model:
            raise RuntimeError("the feature number of src and tgt must be equal to d_model")
        
#         print('ENCODER_STEP')
        memory = self.encoder(src, mask=src_mask, src_key_padding_mask=src_key_padding_mask)
#         print('DECODER_STEP')
        output = self.decoder(tgt, memory, tgt_mask=tgt_mask, memory_mask=memory_mask,
                              tgt_key_padding_mask=tgt_key_padding_mask,
                              memory_key_padding_mask=memory_key_padding_mask)
        return output

    @staticmethod
    def generate_square_subsequent_mask(sz: int) -> Tensor:
        r"""Generate a square mask for the sequence. The masked positions are filled with float('-inf').
            Unmasked positions are filled with float(0.0).
        """
        return torch.triu(torch.full((sz, sz), float('-inf')), diagonal=1)

    def _reset_parameters(self):
        r"""Initiate parameters in the transformer model."""

        for p in self.parameters():
            if p.dim() > 1:
                xavier_uniform_(p)


class TransformerEncoder(Module):
    r"""TransformerEncoder is a stack of N encoder layers. Users can build the
    BERT(https://arxiv.org/abs/1810.04805) model with corresponding parameters.
    Args:
        encoder_layer: an instance of the TransformerEncoderLayer() class (required).
        num_layers: the number of sub-encoder-layers in the encoder (required).
        norm: the layer normalization component (optional).
        enable_nested_tensor: if True, input will automatically convert to nested tensor
            (and convert back on output). This will improve the overall performance of
            TransformerEncoder when padding rate is high. Default: ``True`` (enabled).
    Examples::
        >>> encoder_layer = nn.TransformerEncoderLayer(d_model=512, nhead=8)
        >>> transformer_encoder = nn.TransformerEncoder(encoder_layer, num_layers=6)
        >>> src = torch.rand(10, 32, 512)
        >>> out = transformer_encoder(src)
    """
    __constants__ = ['norm']

    def __init__(self, encoder_layer, num_layers, norm=None, enable_nested_tensor=True):
        super(TransformerEncoder, self).__init__()
        self.layers = _get_clones(encoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm
        self.enable_nested_tensor = enable_nested_tensor

    def forward(self, src: Tensor, mask: Optional[Tensor] = None, src_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the input through the encoder layers in turn.
        Args:
            src: the sequence to the encoder (required).
            mask: the mask for the src sequence (optional).
            src_key_padding_mask: the mask for the src keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """
        for mod in self.layers:
            output = mod(src, src_mask=mask, src_key_padding_mask=src_key_padding_mask)

        if self.norm is not None:
            output = self.norm(output)

        return output


class TransformerDecoder(Module):
    r"""TransformerDecoder is a stack of N decoder layers
    Args:
        decoder_layer: an instance of the TransformerDecoderLayer() class (required).
        num_layers: the number of sub-decoder-layers in the decoder (required).
        norm: the layer normalization component (optional).
    Examples::
        >>> decoder_layer = nn.TransformerDecoderLayer(d_model=512, nhead=8)
        >>> transformer_decoder = nn.TransformerDecoder(decoder_layer, num_layers=6)
        >>> memory = torch.rand(10, 32, 512)
        >>> tgt = torch.rand(20, 32, 512)
        >>> out = transformer_decoder(tgt, memory)
    """
    __constants__ = ['norm']

    def __init__(self, decoder_layer, num_layers, norm=None):
        super(TransformerDecoder, self).__init__()
        self.layers = _get_clones(decoder_layer, num_layers)
        self.num_layers = num_layers
        self.norm = norm

    def forward(self, tgt: Tensor, memory: Tensor, tgt_mask: Optional[Tensor] = None,
                memory_mask: Optional[Tensor] = None, tgt_key_padding_mask: Optional[Tensor] = None,
                memory_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the inputs (and mask) through the decoder layer in turn.
        Args:
            tgt: the sequence to the decoder (required).
            memory: the sequence from the last layer of the encoder (required).
            tgt_mask: the mask for the tgt sequence (optional).
            memory_mask: the mask for the memory sequence (optional).
            tgt_key_padding_mask: the mask for the tgt keys per batch (optional).
            memory_key_padding_mask: the mask for the memory keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """
        output = tgt
#         print('x before decoder')
#         print(output)
        for mod in self.layers:
            output = mod(output, memory, tgt_mask=tgt_mask,
                         memory_mask=memory_mask,
                         tgt_key_padding_mask=tgt_key_padding_mask,
                         memory_key_padding_mask=memory_key_padding_mask)

        if self.norm is not None:
            output = self.norm(output)

        return output

class TransformerEncoderLayer(Module):
    r"""TransformerEncoderLayer is made up of self-attn and feedforward network.
    This standard encoder layer is based on the paper "Attention Is All You Need".
    Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N Gomez,
    Lukasz Kaiser, and Illia Polosukhin. 2017. Attention is all you need. In Advances in
    Neural Information Processing Systems, pages 6000-6010. Users may modify or implement
    in a different way during application.
    Args:
        d_model: the number of expected features in the input (required).
        nhead: the number of heads in the multiheadattention models (required).
        dim_feedforward: the dimension of the feedforward network model (default=2048).
        dropout: the dropout value (default=0.1).
        activation: the activation function of the intermediate layer, can be a string
            ("relu" or "gelu") or a unary callable. Default: relu
        layer_norm_eps: the eps value in layer normalization components (default=1e-5).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).
        norm_first: if ``True``, layer norm is done prior to attention and feedforward
            operations, respectivaly. Otherwise it's done after. Default: ``False`` (after).
    Examples::
        >>> encoder_layer = nn.TransformerEncoderLayer(d_model=512, nhead=8)
        >>> src = torch.rand(10, 32, 512)
        >>> out = encoder_layer(src)
    Alternatively, when ``batch_first`` is ``True``:
        >>> encoder_layer = nn.TransformerEncoderLayer(d_model=512, nhead=8, batch_first=True)
        >>> src = torch.rand(32, 10, 512)
        >>> out = encoder_layer(src)
    Fast path:
        forward() will use a special optimized implementation if all of the following
        conditions are met:
        - Either autograd is disabled (using ``torch.inference_mode`` or ``torch.no_grad``) or no tensor
          argument ``requires_grad``
        - training is disabled (using ``.eval()``)
        - batch_first is ``True`` and the input is batched (i.e., ``src.dim() == 3``)
        - norm_first is ``False`` (this restriction may be loosened in the future)
        - activation is one of: ``"relu"``, ``"gelu"``, ``torch.functional.relu``, or ``torch.functional.gelu``
        - at most one of ``src_mask`` and ``src_key_padding_mask`` is passed
        - if src is a `NestedTensor <https://pytorch.org/docs/stable/nested.html>`_, neither ``src_mask``
          nor ``src_key_padding_mask`` is passed
        - the two ``LayerNorm`` instances have a consistent ``eps`` value (this will naturally be the case
          unless the caller has manually modified one without modifying the other)
        If the optimized implementation is in use, a
        `NestedTensor <https://pytorch.org/docs/stable/nested.html>`_ can be
        passed for ``src`` to represent padding more efficiently than using a padding
        mask. In this case, a `NestedTensor <https://pytorch.org/docs/stable/nested.html>`_ will be
        returned, and an additional speedup proportional to the fraction of the input that
        is padding can be expected.
    """
    __constants__ = ['batch_first', 'norm_first']

    def __init__(self, d_model: int, nhead: int, dim_feedforward: int = 2048, dropout: float = 0.1,
                 activation: Union[str, Callable[[Tensor], Tensor]] = F.relu,
                 layer_norm_eps: float = 1e-5, batch_first: bool = False, norm_first: bool = False,
                 use_norm=True,
                 device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(TransformerEncoderLayer, self).__init__()
        self.self_attn = MultiheadAttention(d_model, nhead, dropout=dropout, batch_first=batch_first,
                                            **factory_kwargs)
        # Implementation of Feedforward model
        self.linear1 = nn.Linear(d_model, dim_feedforward, **factory_kwargs)
        self.dropout = nn.Dropout(dropout)
        self.linear2 = nn.Linear(dim_feedforward, d_model, **factory_kwargs)

        self.norm_first = norm_first
        self.norm1 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.norm2 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)

        
        self.activation = activation
        
        self.use_norm = use_norm

    def __setstate__(self, state):
        if 'activation' not in state:
            state['activation'] = F.relu
        super(TransformerEncoderLayer, self).__setstate__(state)

    def forward(self, src: Tensor, src_mask: Optional[Tensor] = None,
                src_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the input through the encoder layer.
        Args:
            src: the sequence to the encoder layer (required).
            src_mask: the mask for the src sequence (optional).
            src_key_padding_mask: the mask for the src keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """

        # see Fig. 1 of https://arxiv.org/pdf/2002.04745v1.pdf

    
        x = src
        if self.norm_first:
            x = x + self._sa_block(self.norm1(x), src_mask, src_key_padding_mask)
            x = x + self._ff_block(self.norm2(x))
        else:
            x = x + self._sa_block(x, src_mask, src_key_padding_mask)
            if self.use_norm:
                x = self.norm1(x)
#             print('x after self attn, res, norm')
#             print(x)
            x = x + self._ff_block(x)
            if self.use_norm:
                x = self.norm2(x)
            

        return x

    # self-attention block
    def _sa_block(self, x: Tensor,
                  attn_mask: Optional[Tensor], key_padding_mask: Optional[Tensor]) -> Tensor:
        x = self.self_attn(x, x, x,
                           attn_mask=attn_mask,
                           key_padding_mask=key_padding_mask,
                           need_weights=False)[0]
        return self.dropout1(x)

    # feed forward block
    def _ff_block(self, x: Tensor) -> Tensor:
        x = self.linear2(self.dropout(self.activation(self.linear1(x))))
        return self.dropout2(x)


class TransformerDecoderLayer(Module):
    r"""TransformerDecoderLayer is made up of self-attn, multi-head-attn and feedforward network.
    This standard decoder layer is based on the paper "Attention Is All You Need".
    Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N Gomez,
    Lukasz Kaiser, and Illia Polosukhin. 2017. Attention is all you need. In Advances in
    Neural Information Processing Systems, pages 6000-6010. Users may modify or implement
    in a different way during application.
    Args:
        d_model: the number of expected features in the input (required).
        nhead: the number of heads in the multiheadattention models (required).
        dim_feedforward: the dimension of the feedforward network model (default=2048).
        dropout: the dropout value (default=0.1).
        activation: the activation function of the intermediate layer, can be a string
            ("relu" or "gelu") or a unary callable. Default: relu
        layer_norm_eps: the eps value in layer normalization components (default=1e-5).
        batch_first: If ``True``, then the input and output tensors are provided
            as (batch, seq, feature). Default: ``False`` (seq, batch, feature).
        norm_first: if ``True``, layer norm is done prior to self attention, multihead
            attention and feedforward operations, respectivaly. Otherwise it's done after.
            Default: ``False`` (after).
    Examples::
        >>> decoder_layer = nn.TransformerDecoderLayer(d_model=512, nhead=8)
        >>> memory = torch.rand(10, 32, 512)
        >>> tgt = torch.rand(20, 32, 512)
        >>> out = decoder_layer(tgt, memory)
    Alternatively, when ``batch_first`` is ``True``:
        >>> decoder_layer = nn.TransformerDecoderLayer(d_model=512, nhead=8, batch_first=True)
        >>> memory = torch.rand(32, 10, 512)
        >>> tgt = torch.rand(32, 20, 512)
        >>> out = decoder_layer(tgt, memory)
    """
    __constants__ = ['batch_first', 'norm_first']

    def __init__(self, d_model: int, nhead: int, dim_feedforward: int = 2048, dropout: float = 0.1,
                 activation: Union[str, Callable[[Tensor], Tensor]] = F.relu,
                 layer_norm_eps: float = 1e-5, batch_first: bool = False, norm_first: bool = False,
                 use_norm=True,
                 device=None, dtype=None) -> None:
        factory_kwargs = {'device': device, 'dtype': dtype}
        super(TransformerDecoderLayer, self).__init__()
        self.self_attn = MultiheadAttention(d_model, nhead, dropout=dropout, batch_first=batch_first,
                                            **factory_kwargs)
        self.multihead_attn = MultiheadAttention(d_model, nhead, dropout=dropout, batch_first=batch_first,
                                                 **factory_kwargs)
        # Implementation of Feedforward model
        self.linear1 = nn.Linear(d_model, dim_feedforward, **factory_kwargs)
        self.dropout = nn.Dropout(dropout)
        self.linear2 = nn.Linear(dim_feedforward, d_model, **factory_kwargs)

        self.norm_first = norm_first
        self.norm1 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.norm2 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.norm3 = nn.LayerNorm(d_model, eps=layer_norm_eps, **factory_kwargs)
        self.dropout1 = nn.Dropout(dropout)
        self.dropout2 = nn.Dropout(dropout)
        self.dropout3 = nn.Dropout(dropout)

        self.activation = activation
        
        self.use_norm = use_norm

    def __setstate__(self, state):
        if 'activation' not in state:
            state['activation'] = F.relu
        super(TransformerDecoderLayer, self).__setstate__(state)

    def forward(self, tgt: Tensor, memory: Tensor, tgt_mask: Optional[Tensor] = None, memory_mask: Optional[Tensor] = None,
                tgt_key_padding_mask: Optional[Tensor] = None, memory_key_padding_mask: Optional[Tensor] = None) -> Tensor:
        r"""Pass the inputs (and mask) through the decoder layer.
        Args:
            tgt: the sequence to the decoder layer (required).
            memory: the sequence from the last layer of the encoder (required).
            tgt_mask: the mask for the tgt sequence (optional).
            memory_mask: the mask for the memory sequence (optional).
            tgt_key_padding_mask: the mask for the tgt keys per batch (optional).
            memory_key_padding_mask: the mask for the memory keys per batch (optional).
        Shape:
            see the docs in Transformer class.
        """
        # see Fig. 1 of https://arxiv.org/pdf/2002.04745v1.pdf

        x = tgt
        if self.norm_first:
            
            x = x + self._sa_block(self.norm1(x), tgt_mask, tgt_key_padding_mask) 
            
            
            x = x + self._mha_block(self.norm2(x), memory, memory_mask, memory_key_padding_mask)  
            
            x = x + self._ff_block(self.norm3(x))
        else:

            x = x + self._sa_block(x, tgt_mask, tgt_key_padding_mask)
            if self.use_norm:
                x = self.norm1(x)
                
#             print('x after self attn, res, norm')
#             print(x)
             
            x = x + self._mha_block(x, memory, memory_mask, memory_key_padding_mask)
            if self.use_norm:
                x = self.norm2(x)
                
            x = x + self._ff_block(x)
            if self.use_norm:
                x = self.norm3(x)
            
#         print('declayer out')
#         print(x)
        return x

    # self-attention block
    def _sa_block(self, x: Tensor,
                  attn_mask: Optional[Tensor], key_padding_mask: Optional[Tensor]) -> Tensor:
        x = self.self_attn(x, x, x,
                               attn_mask=attn_mask,
                               key_padding_mask=key_padding_mask,
                               need_weights=False)[0]
        return self.dropout1(x)

    # multihead attention block
    def _mha_block(self, x: Tensor, mem: Tensor,
                   attn_mask: Optional[Tensor], key_padding_mask: Optional[Tensor]) -> Tensor:
        x = self.multihead_attn(x, mem, mem,
                                attn_mask=attn_mask,
                                key_padding_mask=key_padding_mask,
                                need_weights=False)[0]
        return self.dropout2(x)

    # feed forward block
    def _ff_block(self, x: Tensor) -> Tensor:
        x = self.linear2(self.dropout(self.activation(self.linear1(x))))
        return self.dropout3(x)

In [9]:
# from https://pytorch.org/tutorials/beginner/transformer_tutorial.html

class PositionalEncoding(nn.Module):

    def __init__(self, d_model: int, dropout: float = 0.1, max_len: int = 5000):
        super().__init__()
        self.dropout = nn.Dropout(p=dropout)

        position = torch.arange(max_len).unsqueeze(1)
        div_term = torch.exp(torch.arange(0, d_model, 2) * (-math.log(10000.0) / d_model))
        pe = torch.zeros(max_len, 1, d_model)
        pe[:, 0, 0::2] = torch.sin(position * div_term)
        pe[:, 0, 1::2] = torch.cos(position * div_term)
        self.register_buffer('pe', pe)

    def forward(self, x: Tensor) -> Tensor:
        """
        Args:
            x: Tensor, shape [seq_len, batch_size, embedding_dim]
        """
        x = x + self.pe[:x.size(0)]
        return self.dropout(x)

In [10]:
class Transformer(Module):
    
    
    def __init__(self, d_model=64, nhead=4, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=512, dropout=0.1, activation=F.gelu, use_norm=False):
        
        super(Transformer, self).__init__()
        self.transformer_model = TransformerModel(d_model=d_model, nhead=nhead, num_encoder_layers=num_encoder_layers,
                                                  num_decoder_layers=num_decoder_layers, dim_feedforward=dim_feedforward,
                                                  dropout=dropout, activation=activation, use_norm=use_norm)
        
        self.pos_encoder = PositionalEncoding(d_model, dropout)
        self.input_projection1 = nn.Linear(1, d_model)
        self.input_projection2 = nn.Linear(d_model, d_model)
        self.output_projection = nn.Linear(d_model, 1)
        
    def forward(self, encoder_x, decoder_x, src_mask=None, tgt_mask=None, memory_mask=None):
        """ encoder_x should be vector of size input_seq_len x bs x 1   
            decoder_x should be vector of size output_seq_len x bs x 1
        """

        
        encoder_x = self.pos_encoder(self.input_projection2(torch.sigmoid(self.input_projection1(encoder_x))))
        decoder_x = self.pos_encoder(self.input_projection2(torch.sigmoid(self.input_projection1(decoder_x))))
        

        x = self.transformer_model(encoder_x, decoder_x, 
                                   src_mask=src_mask, tgt_mask=tgt_mask, memory_mask=memory_mask)
        x = self.output_projection(x)
        return x

    
        
        
        

In [ ]:
# process data for vanilla transformer. I.e. create all possible sequences. Include null values

In [ ]:
series_values = data[0]['series_value']
series_values

In [ ]:
date_range = pd.date_range(start='1996-03-18', periods=791, freq='D')  # can do this because all series have same length
date_range

In [ ]:
# to make it easy, set a default encoder and decoder seq len
encoder_seq_len = 14  # i.e. 2 weeks of data to use in encoder
decoder_seq_len = 7

In [ ]:
# think about rolling cross validation but for now just have one test set at the end
train_set_dates = date_range[date_range < '1998-01-01'] 
test_set_dates = date_range[date_range >= datetime.datetime.strptime('1998-01-01', '%Y-%m-%d') - datetime.timedelta(encoder_seq_len)] 
# i.e. the first dates we want to predict are the week starting from 1998-01-01
# have to make sure these values we want to predict never pop up in the training set, including the decoder inputs
# in other words the latest decoder output should be one day before 1998-01-01 to avoid any leakage


In [11]:
def split_data_into_sequences(data_series, encoder_seq_len, decoder_seq_len, start_date=None, end_date=None, 
                              absolute_start_date='1996-03-18'):
    
    data_series = list(pd.Series(data_series).replace('NaN', np.nan))
    date_range = pd.date_range(start=absolute_start_date, periods=len(data_series), freq='D')
    start_date_idx = date_range.get_loc(start_date) if start_date is not None else 0
    end_date_idx = date_range.get_loc(end_date) if end_date is not None else len(date_range) - 1   

    data_subset = torch.Tensor(data_series[start_date_idx : end_date_idx + 1])
    
    
    sequences_ = []
    for start in range(0, len(data_subset) - decoder_seq_len - encoder_seq_len):
        enc_seq = data_subset[start : start + encoder_seq_len]
        dec_seq = data_subset[start + encoder_seq_len - 1 : start + encoder_seq_len + decoder_seq_len - 1]
        ground_truth = data_subset[start + encoder_seq_len : start + encoder_seq_len + decoder_seq_len]
        if torch.sum(~torch.isnan(ground_truth)).item() > 0:  # sequences with all null ground truth exist. Exclude these model ruiners
            sequences_.append((enc_seq, dec_seq, ground_truth))
            
        
    
#     sequences_ = [(data_subset[start : start + encoder_seq_len],
#                    data_subset[start + encoder_seq_len - 1 : start + encoder_seq_len + decoder_seq_len - 1],
#                    data_subset[start + encoder_seq_len : start + encoder_seq_len + decoder_seq_len])
#                  for start in range(0, len(data_subset) - decoder_seq_len - encoder_seq_len)]
    
    return sequences_


def split_dataset_into_sequences(dataset, encoder_seq_len, decoder_seq_len, start_date=None, end_date=None, 
                                 absolute_start_date='1996-03-18'):
    all_sequences = []
    for time_series in dataset:
        sequences_ = split_data_into_sequences(time_series, encoder_seq_len, decoder_seq_len, start_date=start_date, 
                                               end_date=end_date, absolute_start_date=absolute_start_date)
        all_sequences.extend(sequences_)
    return all_sequences


In [12]:
encoder_seq_len = 14
decoder_seq_len = 7

In [90]:
torch.sum(~torch.isnan(torch.Tensor([np.nan, np.nan, np.nan]))).item() > 0

False

In [ ]:
testing_start_date = datetime.datetime.strptime('1998-01-01', '%Y-%m-%d') 
val_start_date = testing_start_date - datetime.timedelta(days=30*4)
training_end_date = val_start_date - datetime.timedelta(days=1)
val_end_date = testing_start_date - datetime.timedelta(days=1)

In [ ]:
train_sequences = split_dataset_into_sequences(series_values, encoder_seq_len, decoder_seq_len, end_date=training_end_date)

In [ ]:
len(train_sequences)

In [ ]:
val_sequences = split_dataset_into_sequences(series_values, encoder_seq_len, decoder_seq_len, 
                                             start_date=val_start_date, end_date=val_end_date)

In [ ]:
len(val_sequences)

In [ ]:
test_sequences = split_dataset_into_sequences(series_values, encoder_seq_len, decoder_seq_len, start_date=testing_start_date)

In [ ]:
len(test_sequences)

In [ ]:
t = torch.Tensor([1, 2, 3])
i = torch.Tensor([0, np.nan, 1]).isnan().nonzero().squeeze()
torch.cat([t[:i], t[i+1:]])

In [ ]:
torch.Tensor([1]).reshape((1))

In [13]:
def create_null_masks_general(in_seq, out_seq, is_self_attn=True, seq_len_dim=0):
    in_seq_len = in_seq.shape[seq_len_dim]
    out_seq_len = out_seq.shape[seq_len_dim]
    isnan_res = in_seq.isnan().nonzero()
    if len(isnan_res) == 0:
        return torch.zeros((out_seq_len, in_seq_len))
    else:
        null_indices = isnan_res.squeeze()
        if isnan_res.shape[0] == 1:
            null_indices = null_indices.reshape((1,))
        mask = torch.zeros((out_seq_len, in_seq_len)).index_fill_(1, null_indices, float('-inf'))
        if is_self_attn:
            for index in null_indices:
                mask[index, index] = 0  # need this to prevent bug when null is in first position (of decoder self attn)
        return mask
    

In [14]:
def create_null_masks(enc_seq, dec_seq, seq_len_dim=0):
    enc_sa_null_mask = create_null_masks_general(enc_seq, enc_seq, seq_len_dim=seq_len_dim)
    dec_sa_null_mask = create_null_masks_general(dec_seq, dec_seq, seq_len_dim=seq_len_dim)
    dec_enc_null_mask = create_null_masks_general(enc_seq, dec_seq, is_self_attn=False, seq_len_dim=seq_len_dim)
    
    return enc_sa_null_mask, dec_sa_null_mask, dec_enc_null_mask

In [15]:
def create_decoder_sa_causality_mask(n_t):
    return TransformerModel.generate_square_subsequent_mask(n_t)

In [16]:
def generate_transformer_masks(encoder_seq, decoder_seq, seq_length_dim=0):
    encoder_sa_null_mask, decoder_sa_null_mask, decoder_encoder_null_mask = create_null_masks(encoder_seq, decoder_seq, 
                                                                                              seq_length_dim)
    decoder_sa_causality_mask = create_decoder_sa_causality_mask(decoder_seq.shape[seq_length_dim])
    decoder_sa_mask = decoder_sa_null_mask + decoder_sa_causality_mask
    
    return encoder_sa_null_mask, decoder_sa_mask, decoder_encoder_null_mask

In [17]:
class SequenceDatasetForTransformer(Dataset):
    def __init__(self, sequences):
        
        """ sequences should be list of tuples of len 3. 
        First item of a tuple: context (encoder input)
        Second item of a tuple: decoder input
        Third item of tuple: ground truth
        """
        self.sequences = sequences
        
    def __len__(self):
        return len(self.sequences)
    
    def __getitem__(self, idx):
        encoder_input, decoder_input, ground_truth = self.sequences[idx]
        
        encoder_sa_null_mask, decoder_sa_mask, decoder_encoder_null_mask = generate_transformer_masks(encoder_input, 
                                                                                                      decoder_input, 
                                                                                                      seq_length_dim=0)
        ground_truth_null_nans =  ground_truth.isnan().nonzero()
        ground_truth_null_indices = torch.ones(ground_truth.shape)
        null_indices_for_sequence = ground_truth_null_nans[:, 0]
        ground_truth_null_indices[null_indices_for_sequence] = 0
        
        encoder_input = torch.nan_to_num(encoder_input)
        decoder_input = torch.nan_to_num(decoder_input)
        ground_truth = torch.nan_to_num(ground_truth)
        
        return (encoder_input, decoder_input, ground_truth, ground_truth_null_indices,
                encoder_sa_null_mask, decoder_sa_mask, decoder_encoder_null_mask)
    

In [18]:
class SequenceDatasetForTransformerTesting(Dataset):
    def __init__(self, sequences):
        
        """ sequences should be list of tuples of len 3. 
        First item of a tuple: context (encoder input)
        Second item of a tuple: decoder input
        Third item of tuple: ground truth
        """
        self.sequences = sequences
        
    def __len__(self):
        return len(self.sequences)
    
    def __getitem__(self, idx):
        encoder_input, _, ground_truth = self.sequences[idx]
        
        ground_truth_null_nans =  ground_truth.isnan().nonzero()
        ground_truth_null_indices = torch.ones(ground_truth.shape)
        null_indices_for_sequence = ground_truth_null_nans[:, 0]
        ground_truth_null_indices[null_indices_for_sequence] = 0
        
        
        
        return (encoder_input, ground_truth, ground_truth_null_indices)

In [16]:
# def process_batch_nulls(encoder_input, decoder_input, ground_truth):  
#     # need this because null indices for ground truth will be different sizes
#     encoder_input = torch.nan_to_num(encoder_input)
#     decoder_input = torch.nan_to_num(decoder_input)
#     ground_truth_null_nans =  ground_truth.isnan().nonzero().T
#     ground_truth_null_indices = torch.ones(ground_truth.shape)  # need this to remove null elements in gt from loss
#     batch_size = ground_truth.shape[0]
    
#     for b in range(batch_size):
#         null_indices_for_sequence = ground_truth_null_nans[1][ground_truth_null_nans[0] == b]
#         ground_truth_null_indices[b, null_indices_for_sequence] = 0
        
#     ground_truth = torch.nan_to_num(ground_truth)
    
#     return encoder_input, decoder_input, ground_truth, ground_truth_null_indices

In [19]:
def format_input(encoder_input, decoder_input, encoder_sa_null_mask, decoder_sa_mask, decoder_encoder_null_mask, n_heads):
    encoder_sa_null_mask = encoder_sa_null_mask.repeat(n_heads, 1, 1)
    decoder_sa_mask = decoder_sa_mask.repeat(n_heads, 1, 1)
    decoder_encoder_null_mask = decoder_encoder_null_mask.repeat(n_heads, 1, 1)
    
    # need e, d to be of shape Length x bs x 1
    encoder_input = encoder_input.T.unsqueeze(-1)
    decoder_input = decoder_input.T.unsqueeze(-1)
    
    return encoder_input, decoder_input, encoder_sa_null_mask, decoder_sa_mask, decoder_encoder_null_mask

In [20]:
def create_train_val_test_sets(data, training_end_date, val_start_date, val_end_date, testing_start_date,
                              encoder_seq_len, decoder_seq_len):
    train_sequences = split_dataset_into_sequences(data, encoder_seq_len, decoder_seq_len, 
                                                   end_date=training_end_date)
    val_sequences = split_dataset_into_sequences(data, encoder_seq_len, decoder_seq_len, 
                                                 start_date=val_start_date, end_date=val_end_date)
    test_sequences = split_dataset_into_sequences(data, encoder_seq_len, decoder_seq_len, 
                                                  start_date=testing_start_date)
    return train_sequences, val_sequences, test_sequences

In [21]:
testing_start_date = datetime.datetime.strptime('1998-01-01', '%Y-%m-%d') 
val_start_date = testing_start_date - datetime.timedelta(days=30*4)
training_end_date = val_start_date - datetime.timedelta(days=1)
val_end_date = testing_start_date - datetime.timedelta(days=1)

In [22]:
nhead = 4

In [23]:
train_sequences, val_sequences, test_sequences = create_train_val_test_sets(series_values, training_end_date, val_start_date, 
                                                                            val_end_date, testing_start_date,
                                                                           14, 7)
train_dataset = SequenceDatasetForTransformer(train_sequences)
train_dataloader = DataLoader(train_dataset, batch_size=8, shuffle=True)

In [24]:
vanilla_transformer_with_nullmask = Transformer(d_model=64, nhead=nhead, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=256, dropout=0.1, activation=F.gelu)

In [25]:
optimizer = torch.optim.Adam(vanilla_transformer_with_nullmask.parameters())

In [30]:
save_path = '/home/mbaroody/Programming/Time series/NN5/v3-{}.pt'

In [39]:

epoch = 0
# prev_params = None
while True:
    running_loss = 0
    print("Epoch {}".format(epoch))
    for i, data in enumerate(train_dataloader):
        if ((i + 1) % 250 == 0):
            print("Reached batch {}, running_loss was {}".format(i+1, running_loss / 250))
            running_loss = 0
            
        encoder_input, decoder_input, ground_truth, ground_truth_null_indices,\
                encoder_sa_null_mask, decoder_sa_mask, decoder_encoder_null_mask = data
        
        
        encoder_input, decoder_input, encoder_sa_null_mask,\
                decoder_sa_mask, decoder_encoder_null_mask = format_input(encoder_input, decoder_input, encoder_sa_null_mask, 
                                                                          decoder_sa_mask, decoder_encoder_null_mask, nhead)
        optimizer.zero_grad()
        outputs = vanilla_transformer_with_nullmask(encoder_input, decoder_input, encoder_sa_null_mask, decoder_sa_mask, 
                                                    decoder_encoder_null_mask)
        # outputs is shape dec_len x bs x 1
        outputs = outputs.squeeze().T

            
        # delete items that are null in target
        losses_nonull_per_sequence = torch.sum(((outputs - ground_truth) * ground_truth_null_indices) ** 2, 1)
        batch_divide = ground_truth_null_indices.shape[1] - torch.sum(1 - ground_truth_null_indices, 1)
        losses_nonull = torch.mean(losses_nonull_per_sequence / batch_divide)
        
        losses_nonull.backward()
        optimizer.step()
        
#         flag = False
#         for param in vanilla_transformer_with_nullmask.parameters():
#             if torch.sum(torch.isnan(param.data)) > 0:
#                 flag = True
#                 break
#         if flag:
#             print('outputs')
#             print(outputs)
#             print('ground truth')
#             print(ground_truth)
#             print('ground truth null indices')
#             print(ground_truth_null_indices)
#             print('loss a')
#             print(losses_nonull_per_sequence)
#             print('batch divide')
#             print(batch_divide)
#             print('loss')
#             print(losses_nonull.item())
            
#             break
                
#         prev_params = vanilla_transformer_with_nullmask.parameters()
        
        running_loss += losses_nonull.item()

        
    print('Saving')
    torch.save(vanilla_transformer_with_nullmask.state_dict(), save_path.format(epoch))
    epoch += 1
        
    

Epoch 0
Reached batch 250, running_loss was 73.03599977111817
Reached batch 500, running_loss was 50.69700951004028
Reached batch 750, running_loss was 41.87771994781494
Reached batch 1000, running_loss was 36.60844202804565
Reached batch 1250, running_loss was 37.05646192169189
Reached batch 1500, running_loss was 37.133101928710936
Reached batch 1750, running_loss was 35.058937873840335
Reached batch 2000, running_loss was 34.744815811157224
Reached batch 2250, running_loss was 35.490919330596924
Reached batch 2500, running_loss was 33.82575410842895
Reached batch 2750, running_loss was 36.09074656677246
Reached batch 3000, running_loss was 33.20457484817505
Reached batch 3250, running_loss was 33.82931559181213
Reached batch 3500, running_loss was 33.41293079376221
Reached batch 3750, running_loss was 33.63183804512024
Reached batch 4000, running_loss was 34.480533950805665
Reached batch 4250, running_loss was 34.516366176605224
Reached batch 4500, running_loss was 32.01423648834228

Reached batch 2000, running_loss was 30.500821786880493
Reached batch 2250, running_loss was 31.269571327209473
Reached batch 2500, running_loss was 29.8469110660553
Reached batch 2750, running_loss was 28.672202409744262
Reached batch 3000, running_loss was 28.809651374816895
Reached batch 3250, running_loss was 28.629059427261353
Reached batch 3500, running_loss was 27.80919753074646
Reached batch 3750, running_loss was 28.58871251296997
Reached batch 4000, running_loss was 29.249101085662844
Reached batch 4250, running_loss was 30.506778217315674
Reached batch 4500, running_loss was 28.67996919250488
Reached batch 4750, running_loss was 28.060999586105346
Reached batch 5000, running_loss was 29.450410301208496
Reached batch 5250, running_loss was 28.772467542648315
Reached batch 5500, running_loss was 31.28061215209961
Reached batch 5750, running_loss was 29.787938190460206
Reached batch 6000, running_loss was 28.994168886184692
Reached batch 6250, running_loss was 31.16738592338562

KeyboardInterrupt: 

In [26]:
val_dataset = SequenceDatasetForTransformerTesting(val_sequences)
val_dataloader = DataLoader(val_dataset, batch_size=8, shuffle=True)

In [27]:
def create_null_mask_for_batch(in_seq, out_seq, is_self_attn=True):
    in_seq_len = in_seq.shape[1]
    out_seq_len = out_seq.shape[1]
    batch_size = in_seq.shape[0]
    null_indices = in_seq.isnan().nonzero()
    if len(null_indices) == 0:
        return torch.zeros((batch_size, out_seq_len, in_seq_len))
    else:
        mask = torch.zeros((batch_size, out_seq_len, in_seq_len))
        for i in range(batch_size):
            sequence_nulls =  null_indices[null_indices[:, 0] == i]
            sequence_nulls = sequence_nulls[:, 1]
            mask[i].index_fill_(1, sequence_nulls, float('-inf'))
            if is_self_attn:
                for index in sequence_nulls:
                    mask[i, index, index] = 0  # need this to prevent bug when null is in first position (of decoder self attn)
        return mask

In [28]:
def create_decoder_causality_mask_batch(dec_seq_len, bs):
    return TransformerModel.generate_square_subsequent_mask(dec_seq_len).unsqueeze(0).repeat(bs, 1, 1)

In [29]:
def create_batch_masks(enc_seq_batch, dec_seq_batch):
    # should be shape bs x seq_len
    enc_mask = create_null_mask_for_batch(enc_seq_batch, enc_seq_batch, is_self_attn=True)
    dec_sa_null_mask = create_null_mask_for_batch(dec_seq_batch, dec_seq_batch, is_self_attn=True)
    dec_sa_causality_mask = create_decoder_causality_mask_batch(dec_seq_batch.shape[1], dec_seq_batch.shape[0])
    dec_sa_mask = dec_sa_null_mask + dec_sa_causality_mask
    dec_enc_mask = create_null_mask_for_batch(enc_seq_batch, dec_seq_batch, is_self_attn=False)
    
    return enc_mask, dec_sa_mask, dec_enc_mask
    
    
    

In [174]:
# e, g, gi = next(iter(val_dataloader))
# print(e)

# d = e[:, -1].unsqueeze(-1)

# create_batch_masks(e, d)

In [51]:
# vanilla_transformer_with_nullmask_ = Transformer(d_model=64, nhead=nhead, num_encoder_layers=2, num_decoder_layers=2,
#                 dim_feedforward=256, dropout=0.1, activation=F.gelu)
vanilla_transformer_with_nullmask_ = Transformer(d_model=64, nhead=nhead, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=256, dropout=0.1, activation=F.gelu)
vanilla_transformer_with_nullmask_.load_state_dict(torch.load('/home/mbaroody/Programming/Time series/NN5/v3-1.pt'))

<All keys matched successfully>

In [30]:
def evaluate_model(model, eval_dataloader):
    model.eval()
    with torch.no_grad():
        total_loss = 0
        batch_count = 0
        for i, val_data in enumerate(eval_dataloader):  # todo refactor code to make val/test stepthroughs easier, remove redundant


            encoder_input, ground_truth, ground_truth_null_indices = val_data

            decoder_input = encoder_input[:, -1].unsqueeze(-1)
            enc_mask = create_null_mask_for_batch(encoder_input, encoder_input, is_self_attn=True)

            encoder_input = torch.nan_to_num(encoder_input)

            ground_truth = torch.nan_to_num(ground_truth)

            batch_errors = torch.zeros((ground_truth.shape[0], ground_truth.shape[1]))
            batch_predictions = torch.zeros((ground_truth.shape[0], ground_truth.shape[1]))
    #         print('enc input')
    #         print(encoder_input)
    #         print('ground truth')
    #         print(ground_truth)
            for h in range(ground_truth.shape[1]):
                dec_sa_null_mask = create_null_mask_for_batch(decoder_input, decoder_input, is_self_attn=True)
                dec_sa_causality_mask = create_decoder_causality_mask_batch(decoder_input.shape[1], decoder_input.shape[0])
                dec_sa_mask = dec_sa_null_mask + dec_sa_causality_mask
                dec_enc_mask = create_null_mask_for_batch(encoder_input, decoder_input, is_self_attn=False)
                decoder_input_ = torch.nan_to_num(decoder_input)

                encoder_input_, decoder_input_, enc_mask_, \
                    dec_sa_mask, dec_enc_mask = format_input(encoder_input, decoder_input_, 
                                                             enc_mask, dec_sa_mask, 
                                                             dec_enc_mask, nhead)
    #             print('dec in')
    #             print(decoder_input_)
    #             print(dec_sa_mask)
    #             print(dec_enc_mask)
                outputs = model(encoder_input_, decoder_input_, enc_mask_, dec_sa_mask, 
                                                            dec_enc_mask)
    #             print('outputs')
    #             print(outputs)
                if h > 0:
                    timestep_outputs = outputs.squeeze().T[:, h]
                else:
                    timestep_outputs = outputs.reshape(outputs.shape[0], outputs.shape[1]).T[:, h]
    #             print('latest')
    #             print(timestep_outputs)
                batch_predictions[:, h] = timestep_outputs
                timestep_batch_loss = (ground_truth[:, h] - timestep_outputs) ** 2
                batch_errors[:, h] = timestep_batch_loss

                decoder_input = torch.cat((decoder_input, timestep_outputs.unsqueeze(-1)), 1)

            losses_nonull_per_sequence = torch.sum(batch_errors, 1)
            batch_divide = ground_truth_null_indices.shape[1] - torch.sum(1 - ground_truth_null_indices, 1)
            error_nonull = torch.mean(losses_nonull_per_sequence / batch_divide)


            print('batch_predictions')
            print(batch_predictions)
            print('ground truth')
            print(ground_truth)
    #         print('batch error')
    #         print(error_nonull)
            batch_count += 1
            total_loss += error_nonull
        avg_loss = total_loss / batch_count
        return avg_loss

            
      
        

In [31]:
evaluate_model(vanilla_transformer_with_nullmask_, val_dataloader)

NameError: name 'vanilla_transformer_with_nullmask_' is not defined

In [32]:
test_dataset = SequenceDatasetForTransformerTesting(test_sequences)
test_dataloader = DataLoader(test_dataset, batch_size=8, shuffle=True)

In [58]:
evaluate_model(vanilla_transformer_with_nullmask_, test_dataloader)

batch_predictions
tensor([[14.4533, 15.0215, 14.0074, 15.0193, 17.5832, 24.3482, 24.4432],
        [10.8278, 13.0628, 17.2765, 21.4622, 18.0658, 10.1093, 11.2110],
        [13.0939, 11.1450, 11.0837, 11.5120, 16.7141, 25.4750, 25.8301],
        [23.4957,  8.0764, 11.1902, 10.6207, 10.5891, 15.6228, 27.1202],
        [15.3418, 22.7115, 27.4751, 20.8706, 12.3762, 13.7968, 14.0079],
        [17.5687, 27.6394, 41.0251, 33.7790, 15.2059, 18.5604, 17.0168],
        [20.7200, 12.2637, 12.7205, 12.1016, 13.0882, 19.0379, 24.9836],
        [27.1492, 24.5650, 23.8544, 26.6158, 34.9255, 51.7365, 49.1516]])
ground truth
tensor([[13.3088, 16.9253, 13.9663, 15.7549, 21.3966, 21.0153, 27.1831],
        [ 9.3109, 14.2031, 18.6481, 31.6938, 39.2031, 17.5697, 15.6891],
        [15.6102, 12.5460, 11.0731,  9.3372, 17.8985, 25.9469,  7.2856],
        [27.6170,  8.6928, 11.9279,  9.9816, 12.2567, 17.4382, 31.0363],
        [12.6907, 27.6565, 32.4961, 24.3951, 18.6875, 14.7422, 14.7685],
        [19.5949, 2

batch_predictions
tensor([[14.8978, 16.3136, 20.2336, 24.1461, 24.6050, 11.1329, 15.5892],
        [ 7.8543,  9.1375, 10.3501, 13.4615, 13.1107,  7.5598,  7.7805],
        [11.7566, 13.4077, 15.4122, 19.1295, 18.8638, 18.7799, 11.5193],
        [16.8552,  8.7077, 10.9598, 11.2986, 11.5924, 14.2490, 21.5965],
        [13.1606, 16.7871, 21.8607, 23.4526, 21.9684, 14.3408, 14.0190],
        [13.1713, 15.1047,  7.1575,  6.6644,  7.0184,  7.7302, 10.0560],
        [10.7955, 12.9889, 11.2398,  9.9905, 14.4765, 15.8455,  9.7966],
        [11.0346, 12.9461, 16.5782, 24.0102, 22.3471,  7.0541, 11.6226]])
ground truth
tensor([[18.5034, 19.5029, 18.1220, 21.9095, 30.9311, 12.1646, 13.7033],
        [ 8.8243, 11.8753, 10.6391, 16.1625, 16.2415,  6.8254,  7.1673],
        [ 8.8294, 13.2653, 13.2370, 20.3231, 22.9592, 19.3594, 12.7409],
        [26.4729, 10.5997, 10.0342, 11.4940, 10.2446, 15.3603, 17.6749],
        [12.3225, 18.3193, 23.7770, 42.8853, 39.0058, 17.6749, 19.2925],
        [12.9274,  

batch_predictions
tensor([[14.5069, 16.4294, 19.0423, 19.9567, 18.7685,  7.6664, 11.6821],
        [13.4764, 12.5158, 15.0263, 20.9575, 29.1098, 23.9915, 14.1465],
        [13.0518, 14.1040, 14.9801, 22.0641, 29.5771, 25.4113, 14.2302],
        [16.3377, 23.2227, 17.4442,  9.1561, 10.2580, 10.7409, 11.2954],
        [19.1689, 20.6188, 19.1729, 20.5825, 26.8619, 43.0532, 42.1938],
        [18.5519, 25.1770, 36.4902, 34.9946, 18.8222, 20.4139, 19.4498],
        [12.2551, 15.7981, 13.4075, 13.6532, 20.7192, 29.7764, 30.2052],
        [10.0240, 10.3090, 10.8668, 14.3791, 23.6896, 23.4694,  8.0174]])
ground truth
tensor([[10.4734,  9.9065, 13.4070, 19.8696,  3.1746,  4.7052, 19.7137],
        [16.0289,  9.3254, 14.1582, 22.2647, 30.3713, 24.2489, 31.9019],
        [10.7710, 12.5992, 15.5329, 22.3498, 35.7143, 27.5085, 12.8260],
        [16.6241, 35.5300, 35.5159, 15.8730, 15.5612, 11.4938, 13.1378],
        [34.1553, 30.1446, 26.6015, 24.4473,  8.2625, 39.5408, 46.3435],
        [19.5862, 2

batch_predictions
tensor([[38.5417, 29.2367, 15.7918, 16.4912, 16.5205, 18.1200, 26.4376],
        [13.3887, 12.5969, 11.1133, 11.1142, 14.0296, 20.2683, 23.1089],
        [27.8409, 18.8936, 18.5881, 18.4337, 21.6959, 32.6462, 42.8075],
        [14.0320, 14.2593, 15.1548, 19.8968, 25.9192, 18.8390, 14.2052],
        [ 7.7913,  7.8652,  8.1154,  8.2398,  9.5041, 14.4125, 18.1945],
        [24.6042,  8.7783, 12.8458, 11.8793, 12.2271, 18.2001, 28.1769],
        [19.6268, 22.9512,  9.1145, 12.0825, 13.1817, 14.0113, 15.6501],
        [19.1932, 15.9918,  8.1897,  9.0991,  9.9171, 10.4993, 15.5893]])
ground truth
tensor([[49.6173, 35.8560,  0.0000, 12.0607, 22.6616, 19.7279, 26.1763],
        [12.6417, 12.8260, 11.6355, 12.8685, 21.0176, 28.9683, 20.6916],
        [32.4688, 23.2285, 22.8741, 17.8146, 16.9501, 25.2693, 41.2273],
        [18.1973, 12.6559, 20.7766, 22.6616, 31.0516, 35.4592, 14.3707],
        [ 0.0000,  5.1552,  7.7985,  8.0484,  5.8916, 17.6749, 18.0957],
        [28.7698,  

batch_predictions
tensor([[11.6739, 11.1113, 11.3129, 14.1589, 22.3772, 20.5489, 11.3539],
        [10.3037, 10.3026, 10.3585, 12.8391, 19.9579, 19.9792, 10.6826],
        [18.0012, 19.2982,  9.7116,  9.5569,  9.4997,  9.4684, 11.6683],
        [11.7805, 14.1706, 12.4507, 12.8110, 16.3701, 25.7554, 27.8708],
        [ 8.2556, 13.3799, 12.4078, 12.4587, 15.4349, 23.1830, 27.5927],
        [ 9.6926,  6.5360,  7.3758,  9.0925,  9.9726, 13.2618, 19.0171],
        [14.4319, 13.6153, 14.8659, 19.0367, 21.3607, 21.7911, 13.2109],
        [10.8454, 12.0657, 13.0203, 14.1627, 17.1758, 22.2248, 15.4951]])
ground truth
tensor([[12.9252, 12.9110, 11.3095, 12.6417, 25.2268,  0.0000,  0.0000],
        [14.4003,  8.9690,  7.5881, 13.9137, 21.4361, 21.8306,  8.4429],
        [21.7649, 22.1725, 13.0326, 12.1120,  9.9421, 11.0863, 12.1646],
        [ 8.7160, 13.2795,  9.4813, 15.4762, 16.7234, 27.4660, 30.2438],
        [ 5.0879, 12.7126, 13.6054, 12.8968, 20.7341, 24.8299, 29.6769],
        [19.5292,  

...

batch_predictions
tensor([[25.0154, 37.8152, 30.0676, 12.7813, 16.8646, 15.5839, 15.8547],
        [21.7714, 32.2256, 28.3453, 19.4589, 16.8996, 16.4368, 15.5281],
        [24.4613, 12.4221, 12.9733, 12.6297, 13.3124, 19.8593, 27.5301],
        [11.4071, 14.5148, 21.3672, 26.1933,  9.1065, 12.1711, 10.3057],
        [ 7.6483,  7.6453,  7.5828,  7.4292,  8.6146,  9.8110, 13.5433],
        [15.2414, 22.9346, 24.8615, 13.3604, 12.3123, 12.4920, 12.1424],
        [38.4249, 14.0706, 17.3899, 16.7142, 16.9453, 34.0080, 47.9889],
        [ 7.4824,  8.7811,  9.4395, 12.4691, 18.7365, 18.8832,  7.6585]])
ground truth
tensor([[23.9229, 46.4286, 42.1910, 18.3815, 17.5454, 17.4036, 18.4382],
        [16.9218, 45.1105, 25.7795,  0.0000,  9.5096, 17.7721, 18.1264],
        [21.8254, 13.8747, 14.8384, 11.1536, 16.6383, 23.2426, 26.3605],
        [17.5960, 15.7286,  0.0000, 25.1841,  4.3530, 13.1904,  2.3277],
        [ 6.5760,  6.0232,  5.2154,  4.2800,  6.8736,  9.6088,  1.9700],
        [17.1910, 2

batch_predictions
tensor([[ 6.1562,  6.2914,  6.6878,  7.2934,  7.2899,  6.6297,  6.5317],
        [19.0303, 21.5068, 21.1353, 17.6278, 12.0433, 13.1282, 14.2808],
        [32.2234, 32.3039, 18.9059, 19.1471, 19.1907, 18.7603, 22.6626],
        [26.6420, 11.2021, 12.9619, 11.5834, 11.4090, 13.7096, 22.8659],
        [ 7.8889,  8.6508, 10.4183, 15.4846, 17.9990,  6.4163,  7.7386],
        [ 6.3600,  6.6078,  6.8681,  7.5764,  8.3267,  7.8561,  6.5533],
        [32.8806, 38.2315, 23.5839, 15.6326, 16.6486, 15.8411, 18.1166],
        [10.6949, 13.2046, 20.9188, 20.3390,  7.8651,  8.9608, 10.5456]])
ground truth
tensor([[ 6.1650,  6.3492,  8.5317,  9.8073,  7.1570,  4.0675,  6.4059],
        [18.4377, 22.4882, 29.8527, 27.7223, 15.4918, 12.9274, 15.1631],
        [23.3298, 40.5839, 28.4193, 22.5802, 19.2530, 23.0274, 26.1967],
        [23.2378,  5.9442,  8.7980,  0.9469, 18.5692, 12.1120, 21.0547],
        [ 1.5518,  3.2746, 10.7969, 14.6107, 21.8438,  4.2609,  7.0884],
        [ 6.4059,  

batch_predictions
tensor([[11.8271, 15.5177, 17.1061,  8.0092,  7.9763, 10.0012, 11.8039],
        [12.9742, 13.4377, 13.6355, 18.3814, 27.2037, 25.9659, 13.6034],
        [11.6598,  7.1356,  6.7904,  6.8614,  6.7300,  7.6733,  9.7994],
        [13.2431, 16.1362, 18.3032, 20.2019, 26.5673, 25.4616, 13.0977],
        [13.9302, 13.6780, 14.0301, 18.8225, 26.8840, 22.3059, 14.3311],
        [19.7642, 21.6303, 11.6302, 10.2280, 11.5156, 15.2883, 19.3898],
        [39.2040, 39.6392, 42.5666, 47.6323, 47.8589, 46.3924, 44.5607],
        [14.7603, 13.8423, 13.6082, 17.4677, 25.5807, 24.7945, 15.2731]])
ground truth
tensor([[17.1094, 15.3077, 14.9790,  6.7859,  8.9690, 10.0736, 10.5734],
        [20.3515, 15.4195, 16.6100, 27.1259, 30.2579, 35.2749, 12.1032],
        [ 1.9700,  4.1383,  5.1587,  5.7115,  6.0516,  7.0437, 11.2103],
        [18.3588, 10.1131, 19.7791, 19.8185, 26.5255, 29.7212,  4.2346],
        [19.4897, 12.3093, 14.4266, 20.7522, 26.3940, 23.3561, 13.5324],
        [22.3698, 3

batch_predictions
tensor([[15.5344, 14.4086,  7.5856,  7.6552,  8.2001,  8.9719, 13.5641],
        [16.3470, 26.0466, 24.4064,  8.7617, 11.7060, 12.1871, 12.1788],
        [22.3713, 34.3907, 31.8331, 16.0516, 17.4520, 17.0413, 16.0284],
        [15.2387, 19.1074, 26.9512, 20.8976, 10.4109, 13.1951, 13.0762],
        [23.6991, 17.9980, 16.8971, 16.2322, 20.7378, 38.8115, 47.0252],
        [13.8667,  5.7917,  6.0732,  7.1901,  9.0059, 12.3289, 16.2735],
        [11.6864, 12.2096, 11.8078, 13.1173, 24.1732, 30.5411, 18.7328],
        [13.6406, 14.1815, 14.5114, 16.0074, 21.0633, 22.4034, 10.8450]])
ground truth
tensor([[19.1478, 14.7028,  5.7075,  9.3635,  6.1415,  9.0216, 11.9937],
        [18.5429, 27.4987, 28.8795, 11.9279, 16.9253, 13.9006, 13.3877],
        [15.4478, 38.8322, 39.6542, 21.0601, 17.1627, 12.7268, 10.0198],
        [15.3770, 17.4036, 27.3384, 26.0062, 10.7710, 13.0669, 11.3804],
        [32.1712, 18.7358, 18.7075, 15.5329, 24.6032, 31.5334, 45.6491],
        [20.1078,  

tensor(36.1484)

In [34]:
class TransformerVanilla(Module):
    
    
    def __init__(self, d_model=64, nhead=4, num_encoder_layers=3, num_decoder_layers=3,
                dim_feedforward=512, dropout=0.1, activation=F.gelu, use_norm=True):
        
        super(TransformerVanilla, self).__init__()
        self.transformer_model = TransformerModel(d_model=d_model, nhead=nhead, num_encoder_layers=num_encoder_layers,
                                                  num_decoder_layers=num_decoder_layers, dim_feedforward=dim_feedforward,
                                                  dropout=dropout, activation=activation, use_norm=use_norm)
        
        self.pos_encoder = PositionalEncoding(d_model, dropout)
        self.input_projection1 = nn.Linear(1, d_model)
        self.input_projection2 = nn.Linear(d_model, d_model)
        self.output_projection = nn.Linear(d_model, 1)
        
    def forward(self, encoder_x, decoder_x, src_mask=None, tgt_mask=None, memory_mask=None):
        """ encoder_x should be vector of size input_seq_len x bs x 1   
            decoder_x should be vector of size output_seq_len x bs x 1
        """
        encoder_x = self.pos_encoder(self.input_projection2(self.input_projection1(encoder_x)))
        decoder_x = self.pos_encoder(self.input_projection2(self.input_projection1(decoder_x)))
        x = self.transformer_model(encoder_x, decoder_x, 
                                   src_mask=src_mask, tgt_mask=tgt_mask, memory_mask=memory_mask)
        x = self.output_projection(x)
        return x

    
        
        
        

In [40]:
model_v0 = TransformerVanilla(d_model=64, nhead=nhead, num_encoder_layers=2, num_decoder_layers=2,
                dim_feedforward=256, dropout=0.1, activation=F.gelu)
model_v0.load_state_dict(torch.load('/home/mbaroody/Programming/Time series/NN5/transformer_vanilla_robustnull_v2-0.pt'))

<All keys matched successfully>

In [41]:
evaluate_model(model_v0, test_dataloader)

batch_predictions
tensor([[11.4240, 11.7356, 12.1022, 12.5022, 12.9190, 13.3243, 13.6408],
        [30.6787, 31.0758, 31.0345, 30.9378, 30.8638, 30.8237, 30.8084],
        [24.8778, 28.7262, 28.5320, 27.3244, 25.2732, 22.0480, 19.4626],
        [17.6461, 22.5739, 21.3124, 19.0141, 16.4467, 15.1427, 15.2202],
        [17.6647, 22.7957, 23.0727, 22.1033, 20.5371, 18.5566, 17.1777],
        [23.0011, 20.9399, 21.2400, 21.9991, 22.6732, 23.2022, 23.6021],
        [16.7230, 19.8401, 19.2410, 18.3349, 17.5219, 16.9240, 16.5867],
        [23.4345, 30.0252, 29.5433, 27.4890, 23.3897, 18.2426, 18.3207]])
ground truth
tensor([[13.5718, 20.6865,  9.6791,  6.8780,  6.9306,  8.3246, 11.8096],
        [24.9079, 29.5634, 34.5739, 45.1604, 18.3456, 21.1073, 22.9616],
        [15.0085, 27.8770, 36.7772, 37.0890, 21.1026, 15.2920, 16.2557],
        [18.0414, 15.5612, 12.9960, 16.9218, 23.0867, 32.1854, 14.1865],
        [21.3010, 35.1332, 33.7302, 13.0244, 12.7976, 12.6842, 13.4070],
        [30.8107, 2

batch_predictions
tensor([[20.8067, 29.1103, 29.0137, 27.0325, 22.3041, 17.1467, 17.3533],
        [20.4119, 21.0035, 20.8544, 20.5631, 20.3071, 20.1406, 20.0661],
        [18.7933, 19.9496, 19.6146, 19.0784, 18.6161, 18.3035, 18.1501],
        [25.6364, 26.1793, 26.1036, 25.8755, 25.6469, 25.4806, 25.3933],
        [20.4224, 21.5751, 21.3344, 20.8683, 20.4482, 20.1543, 20.0001],
        [16.5220, 15.1254, 15.5129, 16.2160, 16.8156, 17.2842, 17.6458],
        [21.0843, 20.0166, 19.7710, 19.9387, 20.2758, 20.6641, 21.0583],
        [24.3506, 28.5611, 28.0166, 26.7180, 24.9353, 22.3779, 20.2739]])
ground truth
tensor([[ 0.0000,  0.0000, 14.8384, 35.4025, 33.6593,  8.3617, 17.2761],
        [13.0527, 15.3345, 29.7761, 26.7999, 15.3345, 18.1122, 14.6117],
        [13.9795, 11.9411, 15.5576, 25.6575, 24.8816, 12.1778, 10.2841],
        [39.5125,  6.8736,  7.3838, 20.8192, 11.5930, 15.8022, 20.1531],
        [13.4271, 15.5445, 28.0247, 14.8211, 32.1278, 22.5013, 23.4482],
        [10.6786,  

batch_predictions
tensor([[19.3798, 19.5794, 19.5151, 19.3745, 19.2441, 19.1614, 19.1317],
        [13.2030, 12.7601, 12.5901, 12.5640, 12.6394, 12.7661, 12.9356],
        [ 5.0716,  4.3449,  4.3207,  4.3548,  4.3802,  4.3972,  4.4094],
        [21.3347, 22.3822, 22.1543, 21.6611, 21.1784, 20.8125, 20.5986],
        [19.8892, 19.7796, 19.8053, 19.8418, 19.8704, 19.8978, 19.9288],
        [23.1622, 25.5485, 25.1959, 24.4085, 23.5533, 22.7522, 22.1007],
        [30.2627, 27.7034, 27.1310, 27.5492, 28.2811, 29.0354, 29.7161],
        [17.9935, 23.7863, 22.9267, 20.7469, 17.5588, 16.0552, 16.3224]])
ground truth
tensor([[22.5013, 20.5024, 10.5734,  8.8769,  8.6796, 14.2951, 18.6612],
        [ 3.4850,  7.9695,  6.3914,  9.6002, 13.9269, 20.3577, 15.1105],
        [ 5.2721,  7.7239,  7.5113,  7.8656,  8.9569, 14.9660,  9.0703],
        [16.6754, 19.8054, 20.7391, 25.1578, 26.9726, 13.5192, 17.7012],
        [31.5623, 28.9453, 12.6381, 16.4256, 16.9385, 16.7806, 18.3719],
        [19.7279, 2

batch_predictions
tensor([[20.2508, 27.6320, 26.7556, 23.8845, 18.5791, 16.6841, 16.9938],
        [38.2789, 38.2719, 38.2730, 38.2732, 38.2730, 38.2728, 38.2728],
        [27.2057, 27.4831, 27.5000, 27.4149, 27.2873, 27.1776, 27.1157],
        [33.5748, 33.1687, 33.1489, 33.2084, 33.2730, 33.3416, 33.4157],
        [13.6617, 17.3827, 21.8854, 20.6916, 18.5013, 16.0529, 14.6150],
        [27.2129, 23.6230, 24.6123, 25.9462, 27.1088, 28.0112, 28.6583],
        [19.7465, 22.5189, 21.8739, 20.7657, 19.5445, 18.3660, 17.5782],
        [14.6181, 18.3109, 21.6524, 21.6582, 20.8906, 19.9369, 19.0848]])
ground truth
tensor([[16.5308, 18.2272, 17.1357, 25.2367, 37.9143, 25.9732, 12.2699],
        [58.4824, 60.6786, 56.6149, 65.8469, 52.4066, 44.9763, 55.1683],
        [13.8605, 17.7296, 13.3645, 15.6179, 40.0652, 53.6706, 24.0930],
        [29.7761, 38.5913, 18.5232, 19.3594, 23.0584, 26.9558, 38.6480],
        [10.5865,  9.5476, 10.0736, 18.5429, 27.4987, 28.8795, 11.9279],
        [14.3566, 4

batch_predictions
tensor([[26.4438, 34.9929, 37.1497, 36.4311, 34.6646, 31.0433, 25.2181],
        [23.2849, 26.6935, 26.1826, 24.8922, 23.0697, 20.8058, 19.2951],
        [13.6317, 12.8158, 13.3054, 14.0125, 14.6529, 15.0863, 15.3150],
        [13.4826, 17.2232, 20.0377, 20.9034, 20.6201, 20.0474, 19.5135],
        [31.1340, 29.8622, 29.4667, 29.5090, 29.7636, 30.1602, 30.6656],
        [20.8650, 21.4058, 21.2585, 20.9730, 20.7182, 20.5501, 20.4744],
        [19.4218, 18.3223, 18.1901, 18.5944, 19.1965, 19.8561, 20.5217],
        [19.0463, 22.0281, 20.9729, 19.3279, 17.3585, 15.7995, 15.5283]])
ground truth
tensor([[33.3640, 53.8532, 47.3567, 22.7117, 20.9232, 16.7938, 20.8443],
        [ 4.3226, 37.1457, 34.5947, 14.6117, 19.7279, 14.3991, 19.0760],
        [13.5850,  9.9816,  9.6923, 10.8890, 11.6781, 16.1494, 23.4219],
        [ 0.0000, 12.9819, 25.3118,  7.7098,  9.3396, 12.4858, 18.4240],
        [ 8.9164, 16.4256, 14.6370, 31.2599, 58.8901, 47.5802, 12.2830],
        [19.3027, 2

...

batch_predictions
tensor([[19.7079, 21.1487, 20.6311, 19.9035, 19.2437, 18.7436, 18.4513],
        [21.2092, 26.2578, 25.4429, 23.1622, 19.2768, 16.8451, 17.0719],
        [21.3137, 27.3300, 26.3208, 23.7923, 19.2296, 16.5596, 16.8733],
        [13.6585, 16.7017, 19.4812, 18.5223, 17.2685, 16.1352, 15.2386],
        [22.2343, 22.4217, 22.4190, 22.3253, 22.2130, 22.1279, 22.0869],
        [21.4733, 21.4613, 21.4607, 21.4596, 21.4580, 21.4560, 21.4668],
        [17.7892, 22.5658, 23.7495, 21.9313, 18.2385, 15.1352, 14.8216],
        [23.4149, 20.5983, 20.9156, 21.9754, 23.0083, 23.8950, 24.6228]])
ground truth
tensor([[13.0102, 21.1026, 24.3197, 18.2540, 13.8180, 12.7409, 11.8056],
        [17.2902, 12.9677, 12.0890, 24.2347, 28.6848, 41.6525, 22.2222],
        [22.3781, 19.3027, 25.9779, 33.6735, 41.1423,  7.4688, 18.0556],
        [11.0205,  7.5881, 10.5471, 11.3230, 24.2109, 29.6028,  8.2720],
        [39.3740, 16.0179, 18.2930, 21.4624, 14.6633, 21.6728, 28.5113],
        [18.0272, 2

batch_predictions
tensor([[17.5629, 21.5274, 20.0976, 17.7681, 15.1275, 13.9333, 13.9012],
        [38.3899, 38.3587, 38.3666, 38.3698, 38.3711, 38.3720, 38.3730],
        [24.9087, 28.4616, 28.3253, 27.2843, 25.6301, 23.2812, 20.9403],
        [21.8366, 19.4721, 19.5490, 20.4864, 21.4518, 22.3171, 23.0788],
        [17.9087, 17.5730, 17.6024, 17.7250, 17.8526, 17.9649, 18.0606],
        [18.9633, 18.1753, 18.0533, 18.2212, 18.4778, 18.7446, 18.9961],
        [14.6515, 14.2414, 14.3246, 14.5710, 14.8478, 15.0987, 15.2981],
        [19.1450, 19.4013, 19.3383, 19.1968, 19.0711, 18.9932, 18.9636]])
ground truth
tensor([[ 9.1662, 15.3472, 20.3840, 23.9085,  5.0237, 10.7180,  8.3377],
        [42.5039, 56.3388, 23.0668,  0.0000, 29.9579, 43.4377, 46.8701],
        [22.9748, 43.0037, 42.7012, 17.3330, 18.4903, 15.9390, 22.3304],
        [36.0969,  6.7460, 14.0590, 14.7251, 18.8067, 21.1876, 37.0040],
        [26.8141, 26.7432, 17.0777, 12.3441, 15.3628, 13.0102, 21.1026],
        [23.0867, 1

batch_predictions
tensor([[23.5074, 25.8062, 25.4845, 24.5385, 23.2999, 21.9071, 20.6611],
        [11.8905, 13.8543, 16.5695, 17.8503, 16.9927, 16.1418, 15.4808],
        [17.3331, 16.8840, 16.8811, 17.0167, 17.1662, 17.3013, 17.4181],
        [24.4895, 29.5520, 29.0227, 27.5336, 25.2343, 21.7544, 19.7968],
        [10.4884, 11.5283, 12.6438, 14.2265, 16.2702, 16.3914, 15.7870],
        [29.0145, 28.4841, 28.3836, 28.4622, 28.5997, 28.7761, 28.9811],
        [19.0618, 19.7135, 19.3871, 18.8428, 18.3432, 17.9965, 17.8316],
        [18.3967, 22.6904, 22.1921, 21.1268, 19.9289, 18.9009, 18.3013]])
ground truth
tensor([[14.7422, 15.1631, 25.1578, 26.9069, 27.9853, 15.4787, 17.4382],
        [11.3361, 13.3877, 14.4266, 16.2283, 24.3556, 23.2378,  6.5623],
        [11.1961, 12.6701, 15.4337, 15.4195, 15.5612, 27.0408, 17.0210],
        [18.7533, 22.0410, 29.4845, 44.7002, 34.2451, 21.2388, 20.1078],
        [ 9.0986,  6.9728, 11.4371, 20.5074, 17.1202,  4.6910, 10.3175],
        [51.7715, 3

batch_predictions
tensor([[28.6590, 30.1266, 30.1227, 29.7369, 29.2613, 28.8291, 28.5020],
        [30.7605, 36.6681, 36.7319, 36.1108, 35.3245, 34.4918, 33.6482],
        [13.7242, 13.3830, 14.4571, 15.5258, 16.2304, 16.5435, 16.6681],
        [15.7956, 15.8385, 15.8223, 15.7830, 15.7482, 15.7326, 15.7350],
        [15.8835, 19.6559, 20.8388, 20.1222, 19.2337, 18.4131, 17.7684],
        [15.4641, 19.4472, 21.0162, 20.3168, 19.4104, 18.5510, 17.8422],
        [16.3740, 18.6976, 18.2902, 17.3790, 16.4904, 15.7603, 15.2475],
        [20.8158, 20.8549, 20.8480, 20.8057, 20.7582, 20.7297, 20.7279]])
ground truth
tensor([[16.7375, 18.1548, 19.3169, 25.5952, 47.6332, 14.7534,  0.0000],
        [24.8299, 29.9178, 44.8413, 49.2914,  7.4405, 13.5771, 21.7545],
        [18.6612,  4.7212,  7.8248,  9.1399, 10.6128, 11.7964, 23.1983],
        [17.4119, 16.7149,  6.3782,  8.9164, 10.7180, 14.1899, 25.9469],
        [12.0465, 19.2885, 30.4280, 22.6616, 11.3237, 14.3566, 11.1395],
        [11.8359, 1

tensor(75.5777)

In [ ]:
e, d, t, gn, ea, da, dea = se, d, t, gn, ea, da, dea = sequence_iter(dl, 3)
print(gn)

In [ ]:
t = torch.Tensor([[1, np.nan], [2, 2], [np.nan, np.nan]]).isnan().nonzero().T
print(t)
t[1][t[0] == 0]


In [ ]:
d = SequenceDatasetForTransformer(train_sequences)
dl = DataLoader(d, batch_size=8, shuffle=True)

In [ ]:
e, d, t, ea, da, dea = next(iter(dl))

In [ ]:
t

In [ ]:
ea.repeat(3, 1, 1).shape

In [ ]:
process_batch_nulls(e,d,t)

In [ ]:
# testing this vanilla transformer. 
# Note that to batch, examples within a single batch must have same enc and dec input lengths
test_transformer = Transformer()
test_encoder_x = torch.unsqueeze(torch.Tensor([[1, 2, 3], [7, 8, 9]]).T, -1)
test_decoder_x = torch.unsqueeze(torch.Tensor([[0, 4], [0, 10]]).T, -1)
ground_truth = torch.Tensor([[4, 5], [10, 11]]).T
test_dec_output = torch.squeeze(test_transformer(test_encoder_x, test_decoder_x), -1)
# ground truth and output are now output_len x bs
test_loss = F.mse_loss(test_dec_output, ground_truth)
test_loss.backward()


In [ ]:
input1 = torch.Tensor([0, 1, 2, 3, 4])
input2 = torch.Tensor([0, 1, 2, 3, 4])
w1 = torch.nn.Parameter(torch.Tensor([[0, 1, 2, 3, 4],
                                     [0, 1, 2, 3, 4],
                                     [0, 1, 2, 3, 4],
                                     [0, 1, 2, 3, 4], 
                                      [0, 1, 2, 3, 4]]), requires_grad=True)
output1 = input1 @ w1
output2 = input2 @ w1
target1 = torch.Tensor([3, 4, 1, np.nan, 4])
target2 = torch.Tensor([3, np.nan, 1, np.nan, 4])
loss1 = F.mse_loss(output1, target1, reduction='none')
loss_without_nan1 = loss1[~torch.isnan(loss1)]
loss2 = F.mse_loss(output2, target2, reduction='none')
loss_without_nan2 = loss2[~torch.isnan(loss2)]
losses = torch.cat((loss_without_nan1, loss_without_nan2), 0)
final_loss = torch.sum(losses) / (len(loss_without_nan1) + len(loss_without_nan2))
final_loss.backward()


In [ ]:
w1.grad

In [ ]:
input1 = torch.Tensor([2, 1, 2, 3, 4])
input2 = torch.Tensor([3, 1, 2, 3, 4])
w1 = torch.nn.Parameter(torch.Tensor([[5, 1, 2, 3, 4],
                                     [5, 1, 2, 3, 4],
                                     [6, 1, 2, 3, 4],
                                     [8, 1, 2, 3, 4], 
                                      [9, 1, 2, 3, 4]]), requires_grad=True)
output1 = input1 @ w1
output2 = input2 @ w1
target1 = torch.Tensor([3, 4, np.nan, 4, 4])
indices1 = list((~target1.isnan()).nonzero(as_tuple=True))
output1_nonull = output1[indices1]
target1_nonull = target1[indices1]
target2 = torch.Tensor([3, np.nan, 1, np.nan, 4])
indices2 = list((~target2.isnan()).nonzero(as_tuple=True))
output2_nonull = output2[indices2]
target2_nonull = target2[indices2]
loss1 = F.mse_loss(output1_nonull, target1_nonull)
loss2 = F.mse_loss(output2_nonull, target2_nonull)
final_loss = (loss1 + loss2) / 2
final_loss.backward()


In [ ]:
loss1

In [ ]:
# pytorch test

inputs = torch.Tensor([4, 0, 7])
weights_vec1 = torch.nn.Parameter(torch.Tensor([[5, 4, 2], [3, 4, 1], [5, 3, 2], [1, 2, 3]]), requires_grad=True)
weights_vec2 = torch.nn.Parameter(torch.Tensor([[1, 2, 3], [4, 5, 6], [2, 3, 2], [4, 3, 1]]), requires_grad=True)
vec3 = torch.Tensor([[1, 2, 3], [4, 5, 6], [2, 3, 2], [4, 3, 1]])
q = weights_vec1 * inputs
k = weights_vec2 * inputs
logits = (q.T @ k) + torch.Tensor([[0, float('-inf'), 0], [0, float('-inf'), 0], [0, float('-inf'), 0]])
logits = logits / 1000  # div by 1000 just for stability for demonstration
logits.retain_grad()
print('logits: ', logits, '\n')
soft = torch.nn.functional.softmax(logits, dim=1)
soft.retain_grad()
print('softmax: ', soft, '\n')
logits2 = (soft @ vec3.T) @ vec3 + torch.Tensor([[0, float('-inf'), 0], [0, float('-inf'), 0], [0, float('-inf'), 0]])
print('logits2: ', logits2, '\n')
soft2 = torch.nn.functional.softmax(logits2, dim=1)
print('softmax: ', soft2, '\n')
final_m = (soft2 @ vec3.T).T
print('final m: ', final_m, '\n')

final = torch.sum(final_m)  # just to get some scalar value at the end
print('final: ', final, '\n')
final.backward()
print('soft gradients: ', soft.grad, '\n')
print('logits gradients: ', logits.grad, '\n')
print('wq gradients: ', weights_vec1.grad, '\n')
print('wk gradients: ', weights_vec2.grad, '\n')

In [ ]:
# pytorch test

inputs = torch.Tensor([4, 0, 7])
weights_vec1 = torch.nn.Parameter(torch.Tensor([5, 4, 2]), requires_grad=True)
weights_vec2 = torch.nn.Parameter(torch.Tensor([1, 2, 3]), requires_grad=True)
q = torch.unsqueeze(weights_vec1, 1) @ torch.unsqueeze(inputs, 1).T
k = torch.unsqueeze(weights_vec2, 1) @ torch.unsqueeze(inputs, 1).T
q.retain_grad()
k.retain_grad()
logits = (q.T @ k) + torch.Tensor([[0, float('-inf'), 0], [0, 0, 0], [0, float('-inf'), 0]])
logits = torch.cat([logits[:1], logits[2:]]) / 1000  # div by 1000 just for stability for demonstration
logits.retain_grad()
print('logits: ', logits, '\n')
soft = torch.nn.functional.softmax(logits, dim=1)
soft = torch.cat([soft[:1], torch.Tensor([[0, 0, 0]]), soft[1:]])
soft.retain_grad()
print('softmax: ', soft, '\n')
final = torch.sum(torch.prod(soft + 1, dim=0))  # just to get some scalar value at the end
print('final: ', final, '\n')
final.backward()
print('soft gradients: ', soft.grad, '\n')
print('logits gradients: ', logits.grad, '\n')
print('q gradients: ', q.grad, '\n')
print('k gradients: ', k.grad, '\n')
print('wq gradients: ', weights_vec1.grad, '\n')
print('wk gradients: ', weights_vec2.grad, '\n')

In [ ]:
# for decoder w1 -- projecting from scalar to matrix dimensionwise

tens1 = torch.Tensor([1, 2])  # timesteps
tens2 = torch.Tensor([1, 2, 3, 4])  # pos encoding
tens1 = tens1.repeat(4, 1)
tens1.T * tens2

In [ ]:
t1 = torch.Tensor([[1, 2], [1 ,2], [1, 2]])
t2 = torch.Tensor([[1, 4], [2 ,5], [3, 6], [4, 5]])


In [ ]:
t1 = torch.Tensor([[1, 2, 3, 4], [5, 6, 7, 8]])
v = torch.nn.Parameter(torch.Tensor([3, 3.1, 3.2, 3.4]), requires_grad=True)
z = t1 * v
s = F.softmax(z, dim=1)
i_ = torch.multinomial(s, 1).squeeze()
print(i_)
selected = torch.cat((torch.unsqueeze(z[0][i_[0]], -1) , torch.unsqueeze(z[1][i_[1]], -1)))
target = torch.Tensor([4, 8])
l = torch.mean(target - z.T[i_])
l.backward()

In [ ]:
z

In [ ]:
v.grad

In [328]:
l = nn.LayerNorm(4)
t = torch.Tensor([[[1, 2, 3, 4], [2, 4, 6, 8]], [[1, 2, 3, 4], [2, 4, 4.2, 5.3]]])
l(t)

tensor([[[-1.3416, -0.4472,  0.4472,  1.3416],
         [-1.3416, -0.4472,  0.4472,  1.3416]],

        [[-1.3416, -0.4472,  0.4472,  1.3416],
         [-1.5752,  0.1050,  0.2730,  1.1971]]],
       grad_fn=<NativeLayerNormBackward>)

In [333]:
p = PositionalEncoding(64, max_len=5000)
p.pe

tensor([[[ 0.0000e+00,  1.0000e+00,  0.0000e+00,  ...,  1.0000e+00,
           0.0000e+00,  1.0000e+00]],

        [[ 8.4147e-01,  5.4030e-01,  6.8156e-01,  ...,  1.0000e+00,
           1.3335e-04,  1.0000e+00]],

        [[ 9.0930e-01, -4.1615e-01,  9.9748e-01,  ...,  1.0000e+00,
           2.6670e-04,  1.0000e+00]],

        ...,

        [[ 9.5625e-01, -2.9254e-01,  6.4315e-01,  ...,  6.3049e-01,
           6.1813e-01,  7.8608e-01]],

        [[ 2.7050e-01, -9.6272e-01, -5.1133e-02,  ...,  6.3036e-01,
           6.1823e-01,  7.8599e-01]],

        [[-6.6395e-01, -7.4778e-01, -7.1816e-01,  ...,  6.3022e-01,
           6.1834e-01,  7.8591e-01]]])